In [4062]:
import pandas as pd
import json, re
import numpy as np
from IPython.display import display, HTML

In [4063]:
from difflib import SequenceMatcher
from difflib import get_close_matches

def similar(a, b):
    return SequenceMatcher(None, a, b).ratio()

In [4064]:
def replacer(s,d):
    for i in d:
        s=s.replace(i,d[i])
    return s

In [4065]:
from fuzzywuzzy import fuzz
from fuzzywuzzy import process

In [4066]:
megye={'Fehér':'AB', 'Arad':'AR', 'Bukarest':'B', 'Bákó':'BC', 'Bihar':'BH', 'Beszterce-Naszód':'BN',
       'Brassó':'BV', 'Kolozs':'CJ', 'Kovászna':'CV', 'Krassó-Szörény':'CS', 'Hunyad':'HD',
       'Hargita':'HR', 'Máramaros':'MM', 'Maros':'MS', 'Szeben':'SB', 'Szatmár':'SM', 'Szilágy':'SJ',
       'Temes':'TM'}

Import data.gov.ro etalon data

In [4067]:
# gov=pd.read_excel('data/raw/data.gov.ro/datedeschise-retea-2019-2020.xls')
# g2017=pd.read_excel('data/raw/Erdely/norm/2017.xlsx')
# siiir2017=g2017['COD SIIIR'].unique()

In [4068]:
osztalyok=['Óvodás csoportok összesen', 'Óvodások összesen',
       'Kiscsoportok száma', 'Kiscsoportosok', 'Középcsoportok száma',
       'Középcsoportosok', 'Nagycsoportok száma', 'Nagycsoportosok',
       'Vegyes csoportok száma', 'Vegyescsoportosok', 'Elemi osztályok összesen',
       'Elemisek összesen', 'Előkészítő osztályok száma',
       'Előkészítő osztályosok', '1. osztályok száma', '1. osztályosok',
       '2. osztályok száma', '2. osztályosok', '3. osztályok száma',
       '3. osztályosok', '4. osztályok száma', '4. osztályosok',
       'Általános osztályok összesen', 'Általánososok összesen',
       '5. osztályok száma', '5. osztályosok', '6. osztályok száma',
       '6. osztályosok', '7. osztályok száma', '7. osztályosok',
       '8. osztályok száma', '8. osztályosok',
       'Középiskolai osztályok összesen', 'Középiskolások összesen',
       '9. osztályok száma', '9. osztályosok', '10. osztályok száma',
       '10. osztályosok', '11. osztályok száma', '11. osztályosok',
       '12. osztályok száma', '12. osztályosok', '13. osztályok száma',
       '13. osztályosok', '14. osztályok száma', '14. osztályosok']
tanitok=['Tanítók összesen','Képzett tanítók', 'Képzetlen tanítók']
osztalyoki=[0.85,0.86,0.1,0.11,0.2,0.21,0.3,0.31,0.25,0.26,4.5,4.6,0.4,0.41,1,1.1,2,2.1,3,3.1,4,4.1,8.5,8.6,5,5.1,6,6.1,7,7.1,8,8.1,12.5,12.6,9,9.1,10,10.1,11,11.1,12,12.1,13,13.1,14,14.1]

Sort out Nev/Tipus/Profil misalignments

PJ, ST replace with loc name  
ST = STRUCTURA  
PJ = PERSONALITATE JURIDICA  
UT = UNITATE TERITORIALA  

# Main
Initialize

In [4069]:
mgov_clean=json.loads(open('data/clean/mgov_clean.json','r').read())
mparams=json.loads(open('data/clean/mparams.json','r').read())

Run for all counties

In [4070]:
dg=pd.read_excel('data/clean/erdely5_manual.xlsx').drop('Unnamed: 0',axis=1)
m=list(megye.keys())[11] #7CJ 8CV 11HR 13MS
print(m)
# for i,d in enumerate(np.sort(dg[dg['Megye']==m]['Név'].unique())):
#     print(i,d)

Hargita


Automatic recognition of school names: 
- find if telepules substring in school
- if not, append to school name end
- then do matching

In [4071]:
ro={'Ă':'A','Ş':'S','Â':'A','Ș':'S','Ț':'T','Â':'A','Î':'I','Ă':'A','Ţ':'T',
   'Á':'A','É':'E','Í':'I','Ó':'O','Ő':'O','Ö':'O','Ú':'U','Ű':'U','Ü':'U'}
def roman(s):
    return replacer(s,ro)

Cleaner function

In [4072]:
def cleaner(nev,telepules,overwrite_result,gov_clean,gov_parent,convert_ro=True,test=False,verbose=False):
    nev=nev.upper()
    full_replaced=False
    for i in range(50,1,-1):
        nev=nev.replace(i*' ',' ')
    if verbose:print('Upper:',nev)
    if nev in full_replace:
        nev=full_replace[nev]+' '+telepules
        full_replaced=True
    else:
        for s in to_clean_before:
            for i in to_clean_before[s]:
                if i in nev:
                    nev=nev.replace(i,' '+s+' ')
        for i in range(10,1,-1): nev=nev.replace(i*' ',' ')
        if verbose:print('After to_clean_before:',nev)
        for s in to_clean:
            for i in to_clean[s]:
                if i in nev:
                    nev=nev.replace(i,' '+s+' ')
                if convert_ro:
                    if roman(i) in nev:
                        nev=nev.replace(roman(i),' '+s+' ')
        for i in range(10,1,-1): nev=nev.replace(i*' ',' ')
        if verbose:print('After to_clean:',nev)
        for s in to_clean2:
            for i in to_clean2[s]:
                if i in nev:
                    nev=nev.replace(i,' '+s+' ')
                if convert_ro:
                    if roman(i) in nev:
                        nev=nev.replace(roman(i),' '+s+' ')
        for i in range(10,1,-1): nev=nev.replace(i*' ',' ')
        if verbose:print('After to_clean2:',nev)
        for s in to_clean_after:
            for i in to_clean_after[s]:
                if i in nev:
                    nev=nev.replace(i,' '+s+' ')
        for i in range(10,1,-1): nev=nev.replace(i*' ',' ')
        if verbose:print('After to_clean_after:',nev)
    for i in range(50,1,-1): nev=nev.replace(i*' ',' ')
    if len(nev)>3:
        if nev[-2:] in (' S',' T'):
            nev=nev[:-2]
    if not full_replaced:
        #insert location name if warranted
        include_fr=False
        tnev=replacer(nev,  {i:'' for i in list(to_clean.keys())[:to_clean_k]+['#']}).strip()
        fr=fuzz.partial_ratio(telepules,tnev)
        if fr<70: include_fr=True
        #but check if parent location messes up things
        nev=nev.strip()
        for n1 in nev.split(' '):
            if n1 not in list(to_clean.keys())[:to_clean_k]:
                if n1 in gov_parent:
                    if gov_parent[n1]==telepules:
                        include_fr=False
        if include_fr:
            nev=nev+' '+telepules
        for s in list(to_clean.keys())[:to_clean_k]:
            if nev.count(s)>1:
                nev=re.sub(s[::-1],"",nev[::-1],count=1)[::-1]
        if not test:
            nev=nev.replace('#','').replace('#','').replace('#','')
        for i in range(10,1,-1): nev=nev.replace(i*' ',' ')
        nev=nev.strip()
    if verbose:print('After location:',nev)
    for s in to_clean_after_location:
        for i in to_clean_after_location[s]:
            if i in nev:
                nev=nev.replace(i,' '+s+' ')
    for i in range(10,1,-1): nev=nev.replace(i*' ',' ')
    nev=nev.strip()
    if nev in overwrite_result:
        nev=overwrite_result[nev]
    if verbose:print(nev) 
    #replace duplicate occurences of locations in final nev string
    while nev.count(telepules)>1:
        nev=nev.replace(telepules,'',1).replace('  ',' ')
    
    return nev

In [4073]:
# nev='Sc Gimnaziala s'
# telepules='ORMENIS'
# cleaner(nev, telepules, overwrite_result, gov_clean, gov_parent, convert_ro=True, test=True,verbose=True)

Reset gov

In [4074]:
def reset_gov(gov_clean,gov_parent):
    for telepules in dv['Localitate'].unique():
        for g in dv[dv['Localitate']==telepules].T.iteritems():
            nev=g[1]['Denumire'].upper()
            nev=roman(nev)
            telepules=g[1]['Localitate']
            telepules=roman(telepules)
            clean_nev=cleaner(nev, telepules, overwrite_result[m], gov_clean, gov_parent)
            if telepules not in gov_clean: gov_clean[telepules]={} 
            gov_clean[telepules][clean_nev]={'index':g[0],'siiir':g[1]['Cod SIIIR']}
            parent=g[1]['Localitate superioară'].upper()
            parent=roman(parent)
            parent=replacer(parent,{i:'' for i in oras}).strip()
            gov_parent[telepules]=parent
    return gov_clean,gov_parent

Pre-processing inits

In [4075]:
oras=['MUNICIPIU ','MUNICIPIUL ','COMUNA ','ORAS ','ORASUL ',' COM ','ORAŞ ']
gov_clean_start={
    'Fehér': {},
    'Arad': {
        'ARAD':['GRDPLG 16 ARAD']
    },
    'Bukarest': {},
    'Bákó': {
        'FAGET':['GRDNRM FAGET'],
        'GHIMES':['GRDNRM GHIMES']
    },
    'Bihar': {
        'SALONTA':['GRDNRM NR.6 SALONTA','GRDNRM NR.7 SALONTA','GRDNRM NR.9 SALONTA',
                  'GRDNRM NR.10 SALONTA','GRDNRM NR.12 SALONTA'],
        'ORADEA':['LICTEH ANDREI SAGUNA ORADEA'],
        'POCLUSA DE BARCAU':['SPRM POCLUSA DE BARCAU'],
        'SANTAUL MARE':['GRDPLG NR. 2 SANTAUL MARE']
    },
    'Beszterce-Naszód': {
        'FANTANITA':['SPRM FANTANITA'],
        'BRANISTEA':['GRDNRM BRANISTEA'],
        'COLDAU':['SPRM COLDAU'],
        'STRUGURENI':['SPRM STRUGURENI'],
        'FANTANELE':['SPRM FANTANELE'],
        'MALIN':['SPRM MALIN'],
        'VITA':['GRDNRM VITA'],
        'CIRESOAIA':['GRDNRM CIRESOAIA'],
        'BRETEA':['SPRM BRETEA']
    },
    'Brassó': {
        'IONESTI':['GRDNRM IONESTI']
    },
    'Kolozs': {
        'MERA':['GRDNRM MERA'],
        'VISEA':['GRDNRM VISEA'],
        'BONTIDA':['GRDNRM BONTIDA'],
        'CAPUSU MARE':['GRDNRM CAPUSU MARE'],
        'CAPUSU MIC':['GRDNRM CAPUSU MIC'],
        'AGHIRESU-FABRICI':['GRDNRM AGHIRESU-FABRICI'],
        'MACAU':['GRDNRM MACAU'],
        'BAGARA':['GRDNRM BAGARA'],
        'INUCU':['SPRM INUCU'],
        'CHESAU':['SPRM KISS JENO CHESAU','GRDNRM CHESAU'],
        'LUNA DE SUS':['GRDPLG LUNA DE SUS'],
        'TUREA':['SPRM TUREA'],
        'BICALAT':['SPRM BICALAT HUEDIN'],
        'CHEIA':['SGMZ CHEIA'],
        'CLUJ-NAPOCA':['LICTEH EDMOND NICOLAU CLUJ-NAPOCA', 'LICTEH TECHNOFRIG CLUJ-NAPOCA',
                      'GRDPLG DUMBRAVIOARA CLUJ-NAPOCA','GRDPLG UNITARIANA CLUJ-NAPOCA'],
        'COJOCNA':['GRDNRM COJOCNA'],
        'SANMARGHITA':['GRDNRM SANMARGHITA'],
        'CAMPIA TURZII':['GRDNRM ARMONIA CAMPIA TURZII']
    },
    'Kovászna': {
        'DOBOLII DE SUS':['GRDNRM DOBOLII DE SUS','SPRM DOBOLII DE SUS'],
        'LUTOASA':['GRDNRM LUTOASA','SPRM LUTOASA'],
        'TINOASA':['GRDNRM TINOASA','SPRM TINOASA'],
        'SANCRAI':['SPRM SANCRAI'],
        'ZOLTAN':['SPRM BETHLEN KATA ZOLTAN','GRDNRM ZOLTAN'],
        'VALEA SCURTA':['GRDNRM VALEA SCURTA','SPRM VALEA SCURTA'],
        'LUNCA OZUNULUI':['SPRM LUNCA OZUNULUI'],
        'SFANTU  GHEORGHE':['SPRM I.A.S SFANTU GHEORGHE','LICTEH GAMAN JANOS SFANTU GHEORGHE',
                            'GRDNRM CENUSAREASA SFANTU GHEORGHE','SGMZ SPECIALA SFANTU GHEORGHE',
                           'GRDNRM NR. 3 SFANTU GHEORGHE','GRDNRM NR. 6 SFANTU GHEORGHE'],
        #https://ziare.com/sfantu-gheorghe/stiri-actualitate/conducerea-de-la-gaman-janos-se-apara-desfiintarea-putea-fi-evitata-prin-consortiu-2194385
        'MAGHERUS':['SPRM FODOR JANOS MAGHERUS'],
        'TUFALAU':['SPRM TUFALAU'],
        'COMOLAU':['SPRM COMOLAU'],
        'RECI':['SPRM ERDOSI SYLVESTER JANOS RECI'],
        'TARGU SECUIESC':['SPRM TINOASA TARGU SECUIESC','GRDNRM TINOASA TARGU SECUIESC',
                         'GRDNRM NR. 5 TARGU SECUIESC','GRDNRM TARGU SECUIESC'],
        'CERNAT':['GRDNRM NR. 3 CERNAT'],
        'OJDULA':['GRDNRM NR. 1 OJDULA'],
        'BATANII MARI':['SGMZ BENEDEK ELEK BATANII MARI']
    },
    'Krassó-Szörény': {
        'RESITA':['GRDNRM NR. 15 RESITA'] #no info
    },
    'Hunyad': {
        'RACASTIA':['GRDNRM RACASTIE']
    },
    'Hargita': {
        'ALDEA':['GRDNRM ALDEA'],
        'ALEXANDRITA':['GRDNRM ALEXANDRITA'],
        'ALUNIS':['SPRM ALUNIS'],
        'ARVATENI':['GRDNRM ARVATENI'],
        'BETA':['GRDNRM BETA'],
        'BADENI':['GRDNRM BADENI','SPRM BADENI'],
        'CECHESTI':['GRDNRM CECHESTI'],
        'CHILENI':['GRDNRM CHILENI'],
        'CINOD':['SGMZ NR. 5 CINOD BANCU'],
        'CIUMANI':['GRDNRM NR. 6 TORPIKEK CIUMANI'],
        'COMANESTI':['GRDNRM COMANESTI'],
        'COMIAT':['GRDNRM COMIAT'],
        'CRISENI':['GRDNRM CRISENI'],
        'CRISTURU SECUIESC':['GRDNRM NR. 6 BETESTI CRISTURU SECUIESC',
                             'GRDNRM NR. 3 CSILLAGSZEM CRISTURU SECUIESC'],
        'DAIA':['GRDNRM DAIA'],
        'DEJUTIU':['GRDNRM DEJUTIU'],
        'DIAFALAU':['SPRM DIAFALAU'],
        'DITRAU':['GRDNRM NR. 1 DITRAU','GRDNRM NR. 2 DITRAU'],
        'DOBENI':['GRDNRM DOBENI','SPRM DOBENI'],
        'EGHERSEC':['SPRM EGHERSEC','GRDNRM EGHERSEC'],
        'FIRTANUS':['GRDNRM FIRTANUS'],
        'GARCIU':['GRDNRM GARCIU'],
        'GHEORGHENI':['GRDNRM NR. 6 GHEORGHENI','GRDNRM NR. 10 GHEORGHENI',
                     'GRDNRM NR. 8 GHEORGHENI','GRDNRM NR. 9 GHEORGHENI',
                     'GRDNRM NR. 3 GHEORGHENI','GRDNRM NR. 4 GHEORGHENI',
                     'CENTRU NAPSUGAR AZ ESOBEN SCSPC GHEORGHEN',
                     'LICTEH CON DE MASINI GHEORGHENI'],
        'IZVORU MURESULUI':['GRDNRM IZVORU MURESULUI'],
        'IZVORUL TROTUSULUI':['GRDNRM IZVORUL TROTUSULUI'],
        'JOSENI':['GRDNRM MEHECSKE JOSENI','GRDNRM NR. 5 JOSENI',
                 'GRDNRM NR. 6 JOSENI','GRDNRM NR. 2 JOSENI',
                 'GRDNRM NR. 3 JOSENI','GRDNRM NR. 4 JOSENI',
                 'GRDNRM TIPE-TUPA JOSENI','GRDNRM NR. 1 JOSENI',
                 'GRDNRM KOZPONTI JOSENI','GRDNRM ALSZEG JOSENI'],
        'LAZARESTI':['GRDNRM LAZARESTI'],
        'LUNCA DE JOS':['SGMZ NR. 6 VALEA CAPELEI LUNCA DE JOS',
                       'SGMZ NR. 7 VALEA INTUNECOASA LUNCA DE JOS',
                       'GRDNRM NR. 7 VALEA INTUNECOASA LUNCA DE JOS',
                       'GRDNRM GURA VAII RECI LUNCA DE JOS',
                       'SPRM GURA VAII RECI LUNCA DE JOS',
                       'GRDNRM PUNTEA LUPULUI LUNCA DE JOS',
                       'GRDNRM VALEA CAPELEI LUNCA DE JOS',
                       'GRDNRM NR. 2 GARA LUNCA DE JOS',
                       'GRDNRM LUNCA DE JO ANTALOC'],
        'LUNCA DE SUS':['SGMZ NR 4 LUNCA DE SUS',
                       'SPRM IZVORUL TROTUSULUI',
                       'GRDNRM NR. 3 PALTINIS CIUC LUNCA DE SUS',
                       'SPRM PALTINIS LUNCA DE SUS',
                       'GRDNRM VALEA UGRA LUNCA DE SUS'],
        'LUPENI':['GRDNRM LUPENI'],
        'LUTITA':['GRDNRM LUTITA'],
        'MIERCUREA CIUC':['SGMZ NR. 5 JIGODIN MIERCUREA CIUC',
                         'GRDNRM NR. 13 SUBPADURE MIERCUREA CIUC',
                         'GRDNRM NR. 8 SUMULEU MIERCUREA CIUC',
                         'GRDNRM NR. 9 CIOBOTENI MIERCUREA CIUC',
                         'GRDNRM NR. 6 MIERCUREA CIUC',
                         'GRDNRM JIGODIN MIERCUREA CIUC',
                         'SCSPC SFANTA ANA MIERCUREA CIUC',
                         'SPRM HARGHITA BAI MIERCUREA CIUC'],
        'MISENTEA':['GRDNRM NR. 5 MISENTEA'],
        'LELICENI':['GRDNRM NR. 7 LELICENI'],
        'NADEJDEA':['GRDNRM NADEJDEA'],
        'NICOLESTI':['GRDNRM NICOLESTI'],
        'ODORHEIU SECUIESC':['SCSPC FUNDATIA ORBAN ODORHEIU SECUIESC',
                             'SPRM BUDVAR ODORHEIU SECUIESC'],
        'ORASENI':['GRDNRM ORASENI'],
        'OTENI':['GRDNRM OTENI'],
        'PALTINIS':['GRDNRM PALTINIS LUPENI'],
        'POLONITA':['GRDNRM POLONITA'],
        'REMETEA':['SGMZ NR. 6 REMETEA','GRDNRM NR. 5 REMETEA',
                  'GRDNRM NR. 6 REMETEA','GRDNRM NR. 2 REMETEA',
                  'GRDNRM NR. 4 REMETEA','GRDPLG REMETEA'],
        'SANDOMINIC':['GRDNRM NR. 5 SANDOMINIC','GRDNRM NR. 6 SANDOMINIC',
                     'GRDNRM NR. 7 SANDOMINIC','GRDNRM NR. 9 SANDOMINIC',
                     'GRDNRM NR. 1 SANDOMINIC','GRDNRM NR. 2 SANDOMINIC',
                     'GRDNRM NR. 4 SANDOMINIC','SPRM CSERALJA',
                     'GRDNRM HANGYABOLY SANDOMINIC'],
        'SACEL':['SPRM SACEL'],
        'SICLOD':['SPRM SICLOD'],
        'SUB CETATE':['GRDNRM SUB CETATE'],
        'TARCESTI':['SPRM TARCESTI'],
        'TARNOVITA':['GRDNRM TARNOVITA'],
        'ULCANI':['GRDNRM ULCANI'],
        'VACARESTI':['GRDNRM VACARESTI'],
        'VALEA BOROS':['GRDNRM VALEA BOROS'],
        'VALEA GARBEA':['GRDNRM VALEA GARBEA'],
        'VOSLABENI':['SGMZ EBNER JENO IZVORUL MURESULUI VOSLABENI'],
        'RARES':['SPRM RARES'],
        'VALEA RECE':['SPRM PUNTEA LUPULUI']
    },
    'Máramaros': {
        'MANAU':['SPRM MANAU','GRDNRM MANAU']
    },
    'Maros': {
        'NEAGRA':['SPRM NEAGRA'],
        'LUNCA':['GRDNRM LUNCA'],
        'SANTANDREI':['SPRM SANTANDREI', 'GRDNRM SANTANDREI'],
        'LASLAU MIC':['GRDNRM LASLAU MIC'],
        'LASLAU MARE':['GRDNRM LASLAU MARE'],
        'IBANESTI-PADURE':['GRDPLG IBANESTI-PADURE'],
        'IBANESTI':['GRDNRM IBANESTI'],
        'DUBISTEA':['GRDNRM DUBISTEA',' SPRM DUBISTEA'],
        'BALA':['GRDNRM BALA'],
        'ERCEA':['GRDNRM ERCEA','SPRM ERCEA'],
        'DRACULEA':['GRDNRM DRACULEA'],
        'DULCEA':['GRDNRM DULCEA','SPRM DULCEA'],
        'CIPAIENI':['GRDNRM CIPAIENI'],
        'LAURENI':['GRDNRM LAURENI'],
        'SFANTU GHEORGHE':['GRDNRM SFANTU GHEORGHE'],
        'REGHIN':['GRDNRM NR. 5 REGHIN', 'GRDNRM NR. 6 REGHIN'],
        'IDICEL PADURE':['GRDNRM IDICEL PADURE'],
        'IDICEL':['GRDNRM IDICEL'],
        'BUDIUL MIC':['SPRM BUDIUL MIC','GRDNRM BUDIUL MIC'],
        'VALEA RECE':['GRDNRM VALEA RECE'],
        'MAGHERANI':['GRDNRM MAGHERANI'],
        'SILEA NIRAJULUI':['GRDNRM SILEA NIRAJULUI'],
        'VALEA SANPETRULUI':['GRDNRM VALEA SANPETRULUI'],
        'ULIES':['GRDNRM ULIES'],
        'BARDESTI':['GRDNRM BARDESTI'],
        'ORMENIS':['GRDNRM ORMENIS'],
        'TARNAVENI':['GRDPLG NR. 1 TARNAVENI'],
        'BOBOHALMA':['GRDNRM BOBOHALMA', 'SPRM BOBOHALMA'],
        'STEJARENI':['GRDNRM STEJARENI'],
        'RAPA DE JOS':['GRDNRM RAPA DE JOS'],
        'VATAVA':['GRDNRM VATAVA'],
        'ABUS':['GRDNRM ABUS'],
        'BAITA':['GRDNRM BAITA'],
        'BALDA':['GRDNRM BALDA','SPRM BALDA'],
        'BARBOSI':['GRDNRM BARBOSI'],
        'CIPAU':['GRDNRM CIPAU'],
        'COASTA MARE':['GRDNRM COASTA MARE'],
        'CUND':['GRDNRM CUND'],
        'DUMBRAVA':['GRDNRM DUMBRAVA'],
        'FRUNZENI':['GRDNRM FRUNZENI'],
        'HABIC':['GRDNRM HABIC'],
        'IVANESTI':['GRDNRM IVANESTI'],
        'LECHINTA':['GRDNRM LECHINTA'],
        'LOGIG':['SPRM LOGIG'],
        'ROSIORI':['GRDNRM ROSIORI','SPRM PETOFI SANDOR ROSIORI'],
        'LUDUS':['GRDPLG NR. 2 LUDUS'],
        'MARASESTI':['GRDNRM MARASESTI'],
        'MORESTI':['GRDNRM MORESTI'],
        'PETEA':['GRDNRM PETEA'],
        'PETRILACA':['GRDNRM PETRILACA'],
        'POIENITA':['GRDNRM POIENITA'],
        'SANGERU DE PADURE':['GRDNRM SANGERU DE PADURE'],
        'SANTU':['SPRM SANTU'],
        'SALCUD':['GRDNRM SALCUD'],
        'SAUSA':['GRDNRM SAUSA'],
        'SOARD':['GRDNRM SOARD'],
        'SOIMUS':['GRDNRM SOIMUS'],
        'SOMOSTELNIC':['GRDNRM SOMOSTELNIC'],
        'TELEAC':['GRDNRM TELEAC'],
        'URISIU DE JOS':['GRDNRM URISIU DE JOS'],
        'URISIU DE SUS':['GRDNRM URISIU DE SUS'],
        'VALEA FRATIEI':['GRDNRM VALEA FRATIEI'],
        'VISINELU':['GRDNRM VISINELU'],
        'VULCAN':['GRDNRM VULCAN'],
        'TIRGU MURES':['GRDNRM NR. 7 TIRGU MURES', 'GRDNRM NR. 14 TIRGU MURES',
                       'GRDPLG NR. 19 TIRGU MURES','GRDNRM NR. 13 TIRGU MURES',
                       'GRDNRM DACIA TIRGU MURES', 'GRDNRM NR. 19 TIRGU MURES',
                       'GRDPLG NR. 13 TIRGU MURES','LITOLC TIRGU MURES',
                       'GRDPLG NR. 9 TIRGU MURES','GRDPLG NR. 3 TIRGU MURES',
                       'GRDNRM NR. 5 TIRGU MURES','GRDNRM ROZMARIN TIRGU MURES','CENTRUL ROZMARIN TIRGU MURES',
                       'GRDNRM CURCUBEU TIRGU MURES','GRDNRM GEORGE COSBUC TIRGU MURES',
                       'GRDNRM TUDOR VLADIMIRESCU TIRGU MURES'],
        'ADRIANU MARE':['SGMZ ADRIANU MARE'],
        'POARTA':['GRDNRM POARTA'],
        'DELENII':['GRDNRM DELENII', 'SGMZ DELENII'],
        'GAMBUT':['GRDNRM GAMBUT'],
        'CERGHID':['GRDNRM CERGHID'],
        'SOVATA':['SPRM NR.3 SOVATA'],
        'MIERCUREA NIRAJULUI':['GRDNRM NR.1 MIERCUREA NIRAJULUI','GRDPLG MIERCUREA NIRAJULUI'],
        'SANMIHAI DE PADURE':['GRDNRM SANMIHAI DE PADURE'],
        'PUSTA':['SPRM PUSTA'],
        'CHIHERU DE SUS':['GRDNRM CHIHERU DE SUS'],
        'CHIHERU DE JOS':['GRDNRM CHIHERU DE JOS'],
        'TUSIN':['GRDNRM TUSIN', 'SPRM TUSIN'],
        'ATINTIS':['GRDNRM ATINTIS'],
        'TONCIU':['GRDNRM TONCIU'],
        'DAIA':['GRDNRM DAIA'],
        'SUVEICA':['SPRM SUVEICA','GRDNRM SUVEICA'],
        'MAIA':['GRDNRM MAIA'],
        'PADURENI':['GRDNRM PADURENI'],
        'SAMBRIAS':['GRDNRM SAMBRIAS', 'SPRM SAMBRIAS'],
        'SERBENI':['GRDNRM SERBENI'],
        'DROJDI':['GRDNRM DROJDI'],
        'IARA DE MURES':['GRDNRM IARA DE MURES'],
        'PAUCISOARA':['GRDNRM PAUCISOARA'],
        'NADASA':['GRDNRM CACICIU NADASA'],
        'SANGEORGIU DE CAMPIE':['GRDNRM SANGEORGIU DE CAMPIE'],
        'STEJARIS':['GRDNRM STEJARIS','SPRM STEJARIS'],
        'DILEUL NOU':['SPRM DILEUL NOU'],
        'SACADAT':['GRDNRM SACADAT'],
        'GORENI':['GRDNRM GORENI'],
        'MOISA':['GRDNRM MOISA'],
        'TIRIMIA':['GRDNRM TIRIMIA'],
        'CAPALNA DE SUS':['GRDNRM CAPALNA DE SUS'],
        'BAGACIU':['GRDNRM BAGACIU'],
        'SANTANA DE MURES':['SPRM SANTANA DE MURES'],
        'JACODU':['GRDNRM JACODU'],
        'SUPLAC':['GRDNRM SUPLAC'],
        'GRAUSOR':['GRDNRM GRAUSORUL','SPRM GRAUSORUL'],
        'OROSIA':['GRDNRM OROSIA'],
        'OROIU':['GRDNRM OROIU'],
        'SINCAI':['SPRM FANATE SINCAI'],
        'FANATE':['GRDNRM FANATE'],
        'BARA':['GRDNRM BARA'],
        'BEZID':['SPRM BEZID'],
        'MILASEL':['GRDNRM MILASEL'],
        'LEPINDEA':['GRDNRM LEPINDEA'],
        'GOGAN':['GRDNRM GOGAN'],
        'CAMPU CETATII':['GRDNRM CAMPU CETATII'],
        'DUMBRAVIOARA':['LICTEH DUMBRAVIOARA'],
        'MICA':['GRDNRM MICA'],
        'VAIDEIU':['GRDNRM VAIDEIU'],
        'CEUAS':['GRDNRM CEUAS'],
        'ISLA':['GRDNRM ISLA'],
        'ROUA':['GRDNRM ROUA'],
        'CEUASU DE CAMPIE':['GRDNRM CEUASU DE CAMPIE'],
        'MURENI':['GRDNRM MURENI'],
        'PIETRIS':['GRDNRM PIETRIS'],
        'BREAZA':['GRDNRM BREAZA'],
        'NEAUA':['GRDNRM NEAUA'],
        'CIOBOTANI':['GRDNRM CIOBOTANI'],
        'POENITA':['SPRM POENITA'],
        'SANISOR':['GRDNRM SANISOR'],
        'BERENI':['GRDNRM BERENI'],
        'FILPISU MIC':['GRDNRM FILPISU MIC'],
        'FILPISU MARE':['GRDNRM FILPISU MARE'],
        'VADU':['GRDNRM VADU'],
        'DUMITRENI':['GRDNRM DUMITRENI'],
        'TROITA':['GRDNRM TROITA'],
        'PACURENI':['SPRM PACURENI'],
        'FANATELE MADARASULUI':['GRDNRM FANATELE MADARASULUI'],
        'NANDRA':['GRDNRM NANDRA'],
        'COMORI':['GRDNRM COMORI'],
        'BATOS':['GRDNRM BATOS'],
        'PETRILACA DE MURES':['GRDNRM PETRILACA DE MURES'],
        'HODOSA':['GRDNRM HODOSA'],
        'ICLAND':['GRDNRM ICLAND'],
        'MURENI':['GRDNRM MURENI'],
        'ILIESI':['GRDNRM ILIESI'],
        'CECELACA':['GRDNRM CECELACA'],
        'ISTIHAZA':['GRDNRM ISTIHAZA'],
        'EREMIENI':['GRDNRM EREMIENI'],
        'MARCULENI':['GRDNRM MARCULENI'],
        'LARGA':['GRDNRM LARGA'],
        'LUNCA MURESULUI':['GRDNRM LUNCA MURESULUI'],
        'CAMPENITA':['GRDNRM CAMPENITA'],
        'CINTA':['GRDNRM CINTA'],
        'PAINGENI':['GRDNRM PAINGENI'],
        'SOLOCMA':['GRDNRM SOLOCMA'],
        'VALEA':['GRDNRM VALEA'],
        'VADAS':['GRDNRM VADAS'],
        'DILEU NOU':['GRDNRM DILEU NOU'],
        'ERNEI':['GRDNRM ERNEI','SPRM ERNEI'],
        'DUMITRESTII':['GRDNRM DUMITRESTII'],
        'GANESTI':['GRDNRM GANESTI'],
        'CIBU':['GRDNRM CIBU'],
        'TOPA':['GRDNRM TOPA'],
        'MAIAD':['GRDNRM MAIAD'],
        'DEAG':['GRDNRM DEAG'],
        'VALENI':['GRDNRM VALENI'],
        'DAMIENI':['GRDNRM DAMIENI'],
    },
    'Szeben': {},
    'Szatmár': {
        'HRIP':['GRDNRM HRIP'],
        'IRINA':['GRDNRM IRINA'],
        'DARA':['GRDNRM DARA'],
        'CAREI':['SGMZ NR. 3 CAREI'],
        'SATU MARE':['LIARTE SATU MARE']
    },
    'Szilágy': {
        'UILEACU SIMLEULUI':['SPRM UILEACU SIMLEULUI', 'GRDNRM UILEACU SIMLEULUI'],
        'BOZIES':['SPRM BOZIES']
    },
    'Temes': {
        'TIMISOARA':['GRDPLG GERHARDINUM TIMISOARA']
    }
}
gov_parent_start={
    'Fehér': {},
    'Arad': {},
    'Bukarest': {},
    'Bákó': {},
    'Bihar': {},
    'Beszterce-Naszód': {
        'FANTANITA':'MICESTII DE CAMPIE',
        'FANTANELE':'MATEI',
        'BRETEA':'SIEU-ODORHEI'
    },
    'Brassó': {
        'IONESTI':'CATA'
    },
    'Kolozs': {
        'INUCU':'AGHIRESU',
        'CHESAU':'MOCIU',
        'BICALAT':'HUEDIN'
    },
    'Kovászna': {
        'DOBOLII DE SUS':'BOROSNEU MARE',
        'LUTOASA':'MERENI',
        'TINOASA':'LUNGA',
        'ZOLTAN':'GHIDFALAU',
        'VALEA SCURTA':'ESTELNIC',
        'LUNCA OZUNULUI':'OZUN',
        'MAGHERUS':'BELIN',
        'TUFALAU':'TAMASFALAU',
        'COMOLAU':'RECI'
    },
    'Krassó-Szörény': {},
    'Hunyad': {},
    'Hargita': {
        'ALEXANDRITA':'FELICENI',
        'ALUNIS':'MUGENI',
        'ARVATENI':'FELICENI',
        'DEJUTIU':'MUGENI',
        'DIAFALAU':'DEALU',
        'DOBENI':'MUGENI',
        'EGHERSEC':'CIUCSANGEORGIU',
        'FIRTANUS':'AVRAMESTI',
        'MISENTEA':'LELICENI',
        'SACEL':'SOIMUSU MIC',
        'RARES':'MARTINIS',
        'CINOD':'BANCU',
        'SICLOD':'ATID',
        'TARCESTI':'SIMONESTI',
        'OTENI':'FELICENI',
        'BADENI':'MARTINIS'
    },
    'Máramaros': {
        'MANAU':'ULMENI'
    },
    'Maros': {
        'NEAGRA':'LUNCA BRADULUI',
        'SANTANDREI':'MIERCUREA NIRAJULUI',
        'DUBISTEA':'HODAC',
        'ERCEA':'BALA',
        'DRACULEA':'DULCEA',
        'BUDIUL MIC':'CRACIUNESTI',
        'SILEA NIRAJULUI':'MAGHERANI',
        'BARDESTI':'SANTANA DE MURES',
        'BOBOHALMA':'TARNAVENI',
        'STEJARENI':'DANES',
        'RAPA DE JOS':'VATAVA',
        'ROSIORI':'LUDUS',
        'ADRIANU MARE':'GALESTI',
        'POARTA':'FARAGAU',
        'GAMBUT':'BICHIS',
        'CERGHID':'UNGHENI',
        'SANMIHAI DE PADURE':'SACALU DE PADURE',
        'PUSTA':'SINCAI',
        'CHIHERU DE SUS':'CHIHERU DE JOS',
        'TUSIN':'SANPETRU DE CAMPIE',
        'SUVEICA':'ACATARI',
        'MAIA':'BERENI',
        'DROJDI':'BERENI',
        'NADASA':'BEICA DE JOS',
        'SANGEORGIU DE CAMPIE':'SANPETRU DE CAMPIE',
        'STEJARIS':'ACATARI',
        'DILEUL NOU':'SANPAUL',
        'MOISA':'GLODENI',
        'CAPALNA DE SUS':'MICA',
        'GRAUSOR':'VARGATA',
        'OROSIA':'CUCI',
        'MILASEL':'CRAIESTI',
        'PIETRIS':'DEDA',
        'CIOBOTANI':'STANCENI',
        'POENITA':'LIVEZENI',
        'DUMITRENI':'BALAUSERI',
        'PACURENI':'GLODENI',
        'NANDRA':'BICHIS',
        'COMORI':'GURGHIU',
        'PETRILACA DE MURES':'GORNESTI',
        'LARGA':'GURGHIU',
        'LUNCA MURESULUI':'ALUNIS',
        'DILEU NOU':'SANPAUL',
        'CIBU':'FANTANELE',
        'TOPA':'ALBESTI',
        'DEAG':'IERNUT',
        'VALENI':'ACATARI',
        'DAMIENI':'EREMITU',
        'PETECU':'ULIES'
    },
    'Szeben': {},
    'Szatmár': {},
    'Szilágy': {
        'UILEACU SIMLEULUI':'MAERISTE'
    },
    'Temes': {}
}
gov_clean={i:{j:{'index':'New school','siiir':0} for j in gov_clean_start[m][i]} for i in gov_clean_start[m]}
gov_parent=gov_parent_start[m]

Pre-processing overwrites

In [4076]:
overwrite_result={
    'Fehér': {
        'GRDNRM NR 1 BLAJ':'GRDPLG GRDCOP BLAJ',
        'GRDNRM BLAJ':'GRDPLG GRDCOP BLAJ',
        'SGMZ LUNCA MURES':'SGMZ LUNCA MURESULUI'
    },
    'Arad': {
        'GRDPLG CASUTA PITICILOR ARAD':'GRDPLG NR.18 ARAD'
    },
    'Bukarest': {},
    'Bákó': {
        'GRDNRM GHIMES (MAG)':'GRDNRM GHIMES',
        'STRUCT GHIMES-FAGET':'SGMZ FAGET'
    },
    'Bihar': {
        'SPRM CIOCAIA SACUENI':'SPRM FENYES ELEK CIOCAIA',
        'LICTEH SALARD':'SGMZ SZALARDI JANOS SALARD',
        'GRDNRM NR.5 DOLEA':'GRDNRM DOLEA',
        'SGMZ NR. 1 CAPILNA GINTA':'SPRM GINTA',
        'GRDPLG NR.5 TELECHIU':'GRDPLG NR.4 TELECHIU',
        'SGMZ DACIA GRDNRM NR. 9 ORADEA':'GRDNRM NR. 12 ORADEA',
        'SGMZ ANDREI MURESANU ORADEA':'LITOLX EPISCOP ROMAN CIOROGARIU ORADEA', #https://www.bihon.ro/stirile-judetului-bihor/scoala-%E2%80%9Eandrei-muresanu%E2%80%9D-a-fuzionat-cu-liceul-teologic-ortodox-645632/
        'SGMZ GEORGE COSBUC ORADEA':'SGMZ SZACSVAY IMRE ORADEA', #https://bihorstiri.ro/scoala-george-cosbuc-a-murit-traiasca-scoala-szacsvay-imre/
        'SGMZ AL. ROMAN ORADEA':'LICTEH SANITAR VASILE VOICULESCU ORADEA', #http://www.oradea-online.ro/oradea/6/sprimare.htm
        'GRDPLG NR.1 BEIUS':'GRDPLG FLOARE DE COLT BEIUS', #https://www.facebook.com/pg/Gr%C4%83dini%C8%9Ba-cu-Program-Prelungit-Floare-de-Col%C8%9B-Beiu%C8%99-509132849192694/about/?ref=page_internal
        'LITEOR GHERLA':'LITEOR KEMENY ZSIGMOND GHERLA', #https://www.gherlainfo.ro/numele-nou-al-liceului-cu-predare-in-limba-maghiara-din-gherla-a-fost-votat-de-consilieri-video-discutii/
        'GRDNRM BEIUS':'GRDPLG FLOARE DE COLT BEIUS'
    },
    'Beszterce-Naszód': {
        'SPRM (UT) SIEU-ODORHEI':'SGMZ SIEU-ODORHEI',
        'SGMZ S. RODNA':'LICTEH FLORIAN PORCIUS RODNA',
        'SGMZ RODNA':'LICTEH FLORIAN PORCIUS RODNA',
        'SPRM . ST. COCIU':'SGMZ COCIU'
    },
    'Brassó': {
        'GRDNRM NR. 4 FAGARAS':'GRDPLG VOINICELUL FAGARAS', #inferred from years
        'GRDNRM NR. 3 BRASOV':'GRDPLG NR. 3 BRASOV',
        'GRDPLG LUMEA COPIILOR NR. 25 BRASOV':'GRDPLG NR. 25 BRASOV', #remove name for perfect number match
        'GRDPLG CASUTA BUCURIEI NR. 11 BRASOV':'GRDPLG NR. 11 BRASOV', #remove name for perfect number match
        'SGMZ NR. 2 DIACONU CORESI BRASOV':'SGMZ NR. 2 BRASOV' #remove name for perfect number match
    },
    'Kolozs': {
        'SGMZ CONSTANTIN BRANCOVEANU BACIU BACIU':'SGMZ BACIU' #remove name because too long compared to location name
    },
    'Kovászna': {
        'SPRM MARCUSA ST':'SPRM BARABAS MIKLOS MARCUSA',
        'SPRM I.A.S SFANTU GHEORGHE ST':'SCSPC SFANTU GHEORGHE',
        'SPRM I.A.S SFANTU GHEORGHE':'SCSPC SFANTU GHEORGHE'
    },
    'Krassó-Szörény': {},
    'Hunyad': {
        'SGMZ MATEI CORVIN HUNEDOARA':'SGMZ NR. 6 HUNEDOARA' #inferred from years
    },
    'Hargita': {},
    'Máramaros': {
        'LICTEH GRIGORE MOISIL TARGU LAPUS':'LICTEH TARGU LAPUS', #remove name because too long compared to location name
        'SGMZ BAIA MARE':'SGMZ NICOLAE IORGA BAIA MARE', #inferred from years,
        'GRDNRM NR. 26 BAIA MARE':'GRDPLG NR. 30 BAIA MARE' #inferred from parent institution
    },
    'Maros': {
        'DILEU VECHI OGRA':'GRDNRM OGRA',
        'GRDPLG IBANESTI PADURE':'GRDPLG IBANESTI',
        'GRDNRM IDICEL PADURE':'GRDNRM IDICEL',
        'GRDNRM SARMASEL GARA':'GRDNRM SARMASEL',
        'GRDNRM SEULIA DE MURES CUCERDEA':'GRDNRM SEULIA DE MURES',
        'SPRM PETOFI SANDOR ROSIORI -L LUDUS':'SPRM PETOFI SANDOR ROSIORI',
        'SPRM BALDA SARMASU':'SGMZ BALDA',
        'SPRM DUMITRENI BALAUSERI':'SPRM DUMITRENI',
        'SPRM PACURENI GLODENI':'SPRM PACURENI', 
        'SPRM DUBISTEA DE PADURE HODAC':'SPRM DUBISTEA DE PADURE',
        'SPRM SINISOR LIVEZENI':'SPRM SINISOR',
        'SPRM TUSIN SANTU':'SPRM SANPETRU DE CAMPIE',
        'SPRM SUVEICA GRUISOR':'SPRM SUVEICA',
        'SPRM ABUD GHINDARI':'SPRM ABUD',
        'GRDNRM SACARENI ERNEI':'GRDNRM SACARENI',
        'SPRM IDICEL BRANCOVENESTI':'SPRM IDICEL',
        'SPRM HARTAU PANET':'SPRM HARTAU'
    },
    'Szeben': {},
    'Szatmár': {
        'SPRM REMETEA OASULUI ORASU NOU':'SPRM REMETEA OASULUI',
        'PERSJ HODOD':'SGMZ WESSELENYI HODOD',
        'PERSJ APA':'SGMZ VASILE LUCACIU APA',
        'SPRM PETRESTI':'SPRM DR. STEFAN VONHAZ PETRESTI',
        'SGMZ RAKOCZI FERENC SATU MARE':'SGMZ RAKOCZI FERENC NR. 10 SATU MARE', #https://www.facebook.com/ScoalaRakocziFerencIskola/
        'SGMZ .NR.5 SATU MARE':'SGMZ MIRCEA ELIADE SATU MARE', #http://www.satu-mare.ro/subpagina/scoala-cu-cls-i-viii-mircea-eliade
        'SGMZ IULIU COROIANU CRAIDOROLT':'SGMZ CRAIDOROLT' #remove name because too long compared to location name
    },
    'Szilágy': {
        'GRDNRM WESSELENYI ZALAU':'GRDNRM REFORMATA WESSELENYI ZALAU', #http://aracip.eu/UnitatiInvatamant/liceul-reformat-wesselenyi-zalau-11059916
        'GRDPLG PITICII ISTETI ZALAU':'GRDPLG PITICII ISTETI NR. 11 ZALAU', #https://scoli.didactic.ro/gradinita-cu-program-prelungit-nr11-zalau
        'GRDPLG NR.11 ZALAU':'GRDPLG PITICII ISTETI NR. 11 ZALAU',
        'GRDPLG NR.11 S ZALAU':'GRDPLG PITICII ISTETI NR. 11 ZALAU'
    },
    'Temes': {
        'SGMZ EFTIMIE MURGU LUGOJ':'SGMZ EFTIMIE MURGU NR. 5 LUGOJ' #http://aracip.eu/UnitatiInvatamant/scoala-gimnaziala-eftimie-murgu-lugoj-10091645
    }
}
siiir_exceptions=['LICTEH TRANSILVANIA TIRGU MURES']

School name cleaner

In [4077]:
to_clean_before={
    'GRDPLG BABSZEM JANKO':['GRĂDINIȚA ”BABSZEM JANKO” CU PROGR PREL.'],
    'COLGNAT BETHLEN GABOR':['COLEGIUL NATIONAL”BG”'],
}
to_clean={
    'SGMZ':['SCOALA GIMNAZIALĂ','ŞCOALA CU CLASELE I-VIII','ȘCOALA CU CLASELE I-VIII','ŞCOALA GIMNAZIALĂ','SOALA GIMN.',' SC.GIMN.','SCOALA GIMNAZIALA',
           'ȘCOALA GIMNAZIALĂ','SC. G.','SC. GIMN.','SCOALA GIM.','SO8',
           'ŞC GIMNAZIALA','ŞC GIMNAZIALA','ŞCOALA CU CLS. I-VIII','ŢCOALA GIMNAZIALĂ','ȘC.GIM.','ȘCOALA GIMNAZIALA',
           'S08','SC.GIMN.','SCOALA CU CLASELE I-VIII','SCOALA CU CLS.I-VIII','SC.GIMNAZIALA','SCOALA GINAZIALA',
           'SCOALA CU CLASELE I - VIII','ŞCOALA CU CLS I-VIII','ŞC.CU CLS. I-VIII','ŞCOALA GIMNAYIALĂ','ŞC.CU CLS.I-VIII','Ş08',
           'ŞC. CU CLS. I-VIII','SCOALA CU CLS I-VIII','ŞCOALA CU CLS.I-VIII','ŞCOALA GIMNAYIALA', 'ŞCOLALA GIMNAZIALĂ',
           'ŞCOALA GIMNAZIALA','ŞCOALA GIMNAZILĂ','ŞCOALA CU CL.I-VIII','ȘCOALĂ GIMNAZIALA','SC.GEN.',
           'ȘC. GIMN.','ȘC.GIMN.','ȘCOAL GIMNAZIALĂ','ȘCOALA GIIMNAZIALĂ','ȘCOALA GIMNAIALĂ',
           'ŞCOALA GIMN.','SC. GEN.','SCOALA GEN.','SOALA GIMNAZIALA','ŞCOALA GIMNATZIALĂ','ŞC. GEN.','ŞC.GEN.',
           'ŞC. GIMN.','SCOALA GIMAZIALĂ','ŞCOALA CU CLASELE I- VIII','ŞCOALA GMNAZIALĂ','ŞCOALA GIMAZIALĂ',
           'ȘCOALA GIMNAZ.','SCOALA CU CL.I-VIII','SCOALA CU CL.I - VIII','SCOALA NORMALA','ȘCOALA GIM,','ȘCOALA GIM.',
           'FELSŐ NÉPISKOLA','SC. GIM.','SCOALA GENERELA','SC.GIM.','ŞC.GIM.','ŞCOAL GIMNAZIALĂ',
           'ȘCOALA GIMAZIALA','ȘCOALĂ GIMNAZIALĂ','ŞC.GIMN.','SC CU CLS. I-VIII','SCOALA CU CLS. I-VIII',
           'ŞCOALA CU CL. I-VIII.','ȘC. GIMNAZIALĂ','ȘC. GIM.','ŞCOALA CU CL -VIII','ŞC.CU CL.I-VIII','ŞCOALA I-VIII',
           'SC.GIMN','ȘC G.','ȘC GIMN.','SX.GIMN.','ȘC. G . ','ŞC. GIMNAZIALA','ŞC. I-VIII','ŞC.GIMNAZIALA','SCOALAGIMNAZIALA',
           'SCOALA CU CL. I-VIII','SCOALA CU CLASELE I -VIII','SCOALA CU CLASELE I VIII','SCOALA CU CLASELE I-VII',
           'SCOALA CU CLASELEI-VIII','SCOALA GIIMNAZIALA','ŞCOALA GIMANZIALĂ','SCOALA GIM CU PREDARE IN LIMBA MAGHIARA',
            'SCOALA GENERALA CU CL.I-VIII.','SCOALA GENERALA CLASELE I-VIII',
            'SC. CLS. I-VIII','SC. GIMN','SC GEN','SC GIMN','SC. GIMN','SCOALA GIMN','ŞCOALA GIMN','ȘCOALA GIMN','SC GIM',
            'SC. GIMNAZIAL','SC GIMNAZIAL'],
    'SPRM':['ŞCOALA PRIMARĂ ST','SCOALA PRIMARA','SC.PRIMAEA','ŞCOALA CU CL. I-IV','SCOALA PRIMARĂ','ŞCOALA PRIMARĂ','ȘCOALA PRIMARĂ','SO4','SC. PRIM.','SC. PRIMARA','SCOALA CLS. I-IV',
           'ŞC.PRIMARĂ','ŞCOALA CU CLD. I-IV','ŞCOALA CU CLS.  I-IV.','ŞCOALA CU CLS. I-IV','SCOALA CU CLASELE I-IV',
           'ŞCOALA CU CL. I-IV','ŞCOALĂ PRIMARĂ','SC.PRIMARA.','ŞCOALA CU CLASELE I-IV','ŞCOALA PRIMARA','SC.PRIMARA',
           'SCOALA CU CL.I-IV.','SCOALA CU CL.I-IV','SCOALA PROMARA','CLASE PRIMARE','ALSÓ NÉPISKOLA','ȘCOALĂ PRIMARĂ','SC.PRIM.',
           'SCOALA PRIMARE','SCOALA PRIMARIA','SCOLA PRIMARA','SCOAL PRIMARA','SCOALA CL.I-IV','SCOALA CU CLS I-IV',
           'ST-ȘCOALA PRIMARA','ȘCOALA PRIMARA','ŞC.PRIM.','ŞC.PRIMARA','ŞCOALAPRIMARA','ŞCOASLA PRIMARĂ','ȘC. PRIMARĂ',
           'ŞCOALA PRIMAR','ŞCOLA PRIMAR','ȘCOALA PRIMARLĂ','SC.CL.I-IV','SC.CL I-IV','SC.CL. I-IV','SC.CLS.I-IV',
           'SC. CL.I-IV','SC. I-IV','SC. PRIMARĂ','SC.I-IV','SC.PEIMARA','SC.LC.I-IV','ȘCOLALA PRIMARĂ','ŞC.CU CL. I-IV',
           'SCOALAPRIMARA','SVÂC.PRIMARA','ŞC. PRIMARĂ','ŞCOALA PRIMATĂ','S04','SCOALA CU CL. I-IV',
           'SCOALA CU CLASELE I - IV','SCOALA CU CLS. I-IV','ŞCOALA CU CLS.I-IV','ȘCOALA CU CLS.I-IV','SC. CLS. I-IV',
           'SCOALA GENERALA CU CL.I-IV.','SCOALA GENERALA CU CL.I-IVI.','SCOALA GENERALA I-IV',
            'SC PRIM','SC.PR','SCOALA PRIM','SCOALA GENERALA CU CLS . I- IV'],
    'SPSTL':['SCOALA POSTLICEALA','SCOALA SANITARA POSTLICEALA','ŞCOALA POSTLICEALĂ','ȘCOALA POSTLICEALĂ',
             'ŞCOALA SANITARĂ POSTLICEALĂ',
            'ȘCOALA POSTLICEALA','ȘCOALA SANITARĂ POSTLICEALĂ','ȘCOALA TEHNICĂ POSTLICEALĂ',
            'SCOALA POSTLICEALĂ'],
    'LICTEH':['COLEGIUL ECONOMIC','COLEGIUL TEHNIC','SCOALA PROFESIONALA','LIC. TEH.AGRICOL','LICEUL TEHN OLOGIC',
             'COLEGIUL TEHNOLOGIC','ŞCOALA PROFESIONALĂ','COLEGIUUL TEHNIC','LIC.TEHN.','COL.EC,,','LICEUL VOCATIONAL',
             'ȘCOALA PROFESIONALĂ','COLEGIUL AGRICOL','LIC. TEH.AGRICOL','LICEUL TEHN.AGR.','LICEU TEHNOLOGIC','COL.EC.','COL.EC .','COL. EC.',
             'COL.TEHN.DE','L.VOC.','LIC.TEH.','LIC.TEHNOL.','LICE. TEHNOLOGIC','LICEUL TEHNOLOGIC AGRICOL','LIC. TEHNOLOGIC','LICEUL TEHNOLOGIC',
             'LICEUL TEHN.','LICEUI TEHN.','LIC.TEHNOLOGIC.','LICEUL TEHOLOGIC','LIC. TEHN','LIC TEHN','C.T.','GRUP SCOLAR AGRICULTURA ECOLOGICA'],
    'LISPRT':['LICEUL CU PROGRAM SPORTIV','CLUBUL SPORTIV SCOLAR','CLUB SPORTIV SCOLAR','CLUBUL SPORTIV ȘCOLAR',
             'CLUBUL ȘCOLAR SPORTIV','LICEUL VOCATIONAL CU PROGRAM SPORTIV','CLUBUL SPORTIV ŞCOLAR',
             'LICEUL SPORTIV','LPS ','L.P.S'],
    'GRDCOP':['CLUBUL COPIILOR','CLUBUL ELEVILOR'], #'PALATUL COPIILOR','LUMEA COPIILOR',
    'LITEOR':['LICEUL NAŢIONAL','LIC.TEO.','LIC. TEOR.','LIC.TEOR.','LICEUL TEORTIC','LIC. TEORETIC',
              'LICEUL TEORETIC','LIC T.','LIC.TEORETIC .','LIC.TEORETIC'],
    'LIPDGA':['LICEUL PEDAGOGIC','LICEUL VOCATIONAL PEDAGOGIC','LICEUL VOCAȚIONAL PEDAGOGIC','LICEUL VOCAŢIONAL PEDAGOGIC'],
    'LITOLU':['LICEUL TEOLOGIC "BAPTIST"','LICEUL TEOLOGIC BAPTIST','LICEUL UNITARIAN','LICEUL TEOLOGIC GRECO-CATOLIC'],
    'LITOLC':['LICEUL TEOLOGIC ROM CAT.','LIC.ROM.CAT.','LIC.TEOL.ROM.',
             'LICEUL ROMANO CATOLIC','LICEUL TELOGIC ROMANO CATOLIC','LICEUL TEOL.ROM.CAT.',
             'LICEUL TEOLOGIC ROMANO CATOLIC','LICEUL TEOLOGIC ROMANO-CATOLIC','LICEUL ROM CAT'],
    'LITOLR':['LICEUL REFORMAT','COLEGIUL REFORMAT','LIC.VOCATIONAL REFORMAT','LICEUL VOCAȚIONAL REFORMAT',
              'LICEUL VOCAŢIONAL REFORMAT','LICEUL VOCATIONAL REFORMAT','ŞCOALA REFORMATĂ CU PEDAGOGIE'],
    'LITOLX':['LICEUL ORTODOX'],
    'LITOLG':['SEMINARUL TEOLOGIC','LIC. TEOL.','LICEUL TEOLOGIC'],
    'LIARTE':['COLEGIUL DE MUZICĂ','LICEUL DE MUZICA','LICEUL DE MUZICĂ','LICEUL DE ARTA','COLEGIUL DE ARTE',
             'LICEUL DE ARTE - PROGRAM SUPLIMENTAR DE MUZICA','LICEUL DE ARTE','LICEUL VOCAȚIONAL DE ARTĂ',
             'LICEUL DE ARTĂ','LIC. VOC.DE ARTA','LIC. DE ARTA','LIC.VOCATIONAL DE ARTA','LICEUL VOCATIONAL DE ARTA',
             'SCOALA DE ARTE SI MESERII'],
    'COLGNAT':['COLEGIUL NAŢIONAL','ŞCOALA NAŢIONALĂ','COL.NAŢ.','COL. NAT.','COLEGIUL NATIONAL',
              'COLEGIUL NAȚIONAL','COL. NAȚ.','COLEGIUL NAT.','COLEGIULNAŢIONAL','COLEGIUL NAŢIOANL','COL.NAT.',
              'COL. NAŢ.','SCOALA NATIONALA','ŞC MILITARĂ','COLEGIU NATIONAL','COL NAT','C.N.'],
    'GRDNRM':['GRADINITA CU PROGRAM NORMAL','GRĂDINITA CU PROGRAM NORMAL','GRĂDINIŢA CU PROGRAM NORMAL','GRĂDINIŢA CU PROGRAM SĂPTĂMÂNAL',
             'GRADINITA CU PROGRAM SAPTAMANAL','GRĂDINIȚA CU PROGRAM SAPTAMANAL','GRĂDINIȚA CU PROGRAM SĂPTĂMÂNAL',
             'GRĂDINIŢĂ CU PROGRAM NORMAL','GRĂDINIȚA CU PROGRAM NORMAL','GRAD.CU PROGRAM NORMAL','GRĂDINŢA CU PROGRAM NORMAL',
             'GRĂNIȚA CU PROGRAM NORMAL','GRADINITA CU PN','GRĂDINIŢA PN','GRĂDINIŢA PN','GRĂDINIŢĂ PN','G.P.N.',
             'GRADINIȚA CU PROGRAM NORMAL','GRĂDINIȚĂ CU PROGRAM NORMAL','GRAD CU PN','GRADINIŢA PN','GRĂD. CU PROGR. NORMAL',
             'GRADINITA CU P.N.','GRĂDINIŢA CU P.N.','GRĂDINIŢA CU PN','GRADINITA CU PROGR. NORMAL',
             'GRADINITA CU PROGRAMNORMAL','GRADINITA CU PROGRM NORMAL','GRĂDINIȚA CU PROPGRAM NORMAL','GRADINITA CU P.N',
             'GRĂDINIŢA CU PROG.NORMAL','GRĂDINIŢA CU PROGRAM NORNAL','GRADINITA CU PROGAM NORMAL','GRAD.PROG.NORMAL',
              'GRĂDINIŢA P.N.','GRĂDINIȚA CU PROGRAN NORMAL','GRADINITA CU PROGRASM NORMAL','GR.P.N.','GRAD P.N.',
             'GRAD. CU PROGRAM NORMAL','GRD CU PROGRAM NORMAL','GGĂDINIȚA CU PROGRAM NORMAL','GRADINTA CU PN','GRĂDINŢIA CU PROGRAM NORMAL',
             'GRADINITA DE COPII CU PROGRAM NORMAL','GRADINITA CU PRORGAM NORMAL','GRĂD.CU PROGR.NORM','GRADINITA DE COPII CU PN',
             'GRADINIŢA CU PROGRAM NORMAL','GRĂDCU PROGR.NORM','GRAD. CU PROG. NORMAL','GRĂDINIȚA PN','GRADINITA PN','GRAD.P.N.',
             'GRĂDINIȚA CU PR. NORMAL','GRADINITA DE COPII CU PRORAM NORMAL','G. P.N.','GRAD PN','GRĂD PN','GAD.P.N.','GRAD CU P.N.'
             'GRAD CU PR NORMAL','GRAD CU P.N.','GRAD CU PR. NORMAL','GRAD. CU P.N.','GRAD. P.N.','GRĂDINIȚA CU PN','GRAD. PN.',
             'GRAD. CU PR. NORMAL','GRAD.P. N.','GRAD.P.N.','GRAD.P.N','GRD.P.N.','GRAD.PN','GRADINITA P.N.','GRADINITA P.N',
             'GRADINITA PG.NORMAL.','GRADINITA PG.NORMAL','GRADINIŢA CU PN','GRAD.CU P N.','GRĂD.CU P.N.','GRADINITA PROG. NORMAL',
             'GR.PN.','GRAD.CU P.N.','GRĂD CU PR NORMAL','G.P.N','GRADDINITA CU PROGRAM NORMAL','GRADINTA CU PROGRAM NORMAL',
             'GRADINITA CU PRGRAM NORMAL','GRADINITA CUPROGRAM NORMAL','GNP','GPN','GRADINITA CU PROGR.NORM'],
    'GRDPLG':['GRADINITA CU PROGRAM PRELUNGIT','GRĂDINIŢA CU PROGRAM PRELUNGIT','GRĂDINIŢA PARTICULARĂ CU PROGRAM PRELUNGIT',
             'GRĂDINIȚA CU PROGRAM PRELUNGIT','G.P.P.','GPP','GRĂDINȚA CU PROGRAM PRELUNGIT','GRAD. CU PROGR. PRELUNGIT',
             'GRĂDINIŢA PP','GRADINITA PP','GRADINIȚA CU PROGRAM PRELUNGIT','GRĂDINIȚÁ CU PROGRAM PRELUNGIT','GRĂDINIȚĂ CU PROGRAM PRELUNGIT',
             'GRĂD. CU PROGR. PRELUNGIT','GRADINITA CU PP','GRĂDINIŢA CU PP',"GR[DINI'A CU PROGRAM PRELUNGIT",'GRADINITA CU P.P.',
             'GRĂDINIŢA CU P.P.','GRĂDINIȚA CU P.P.','GRĂDINIȚA CU PP','GRADINITACU P.P.','GRAD.CU P.P.','GRĂDINIŢA CU P. P.',
              'GRĂDINIŢA P.P.','GRĂDINIŢĂ CU PROGRAM PRELUNGIT','GRADINIȚA AU PROGRAM PRELUNGIT','GRĂDINIŢA CU PROGRM PRELUNGIT',
             'GRĂDINIŢA CU P.P','GRĂDINITA CU PROGRAM PRELUNGIT','GRAD. CU PR PRELUNGIT','GRAD. CU PR. PREL.','GRĂD.PROGR. PRELUNGIT',
             'GRAD. CU PR. PRELUNGIT','GRAD. CU PROGRAM PRELUNGIT','GRĂDINIŢA CU PR.PR.','GRĂDINIŢA CU PROG.PREL.','GRADINITA DE COPII PR.PRELUNGIT',
             'GRAD. CU PROG. PRELUNGIT','GRAD. PP','GR.PP.','GRĂDINIȚA PP','GR P.P.','GAD.P.P.','GPP','GR.P.P','GRAD P.P.','GRAD CU P.P.','GRAD CU P.P',
             'GRAD. CU P.P.','GRAD. P. P.','GRAD. P.P.','GRAD. P.P','GRAD.P.P.','GRAD.P.P','GRADINITA CU PR.PR.','GRADINITA PG.PREL.',
             'GRĂD.CU P.P.','GRADINITA PROG. PREL.','GRĂD PP','GRĂD CU PR PREL','G.P.P','GRADINITA CU PROGR.PREL.','GRĂDINIȚA CU PROGRAMPRELUNGIT',
             'GRAD CU PR PRELUNGIT','GRĂDINITA CU PRGRAM PRELUNGIT','GRADINITA P.P','GR P.P'],
    'GRPSC':['GRUP SCOLAR','G.Ş.','GRUPUL SCOLAR','GRUPUL ŞCOLAR','GRUPUL ȘCOLAR',
            'GR.SC. AGROIND.','GR.SC. EC.ADM.','GRUP ŞCOLAR','GRUPUL SC.AGR.IND.ALIM.','GRUPUL SC.EC.ADM.','GRUP SC.',
            'GR. SC.','GR.SC.','GR,ŞC.','GR. ŞC.'],
    'INSPSCJ':['INSPECTORATUL ŞCOLAR JUDEŢEAN','INSPECTORATUL ȘCOLAR JUDEȚEAN','CASA CORPULUI DIDACTIC','CENTRUL JUDETEAN DE RESURSE',
              'CENTRUL JUDEŢEAN DE RESURSE','CENTRU JUDEŢEAN DE RESURSE','CENTRUL JUDEȚEAN DE RESURSE','CENTRUL JUDEȚEAN DE EXCELENȚĂ',
              'INSPECTORATUL SCOLAR JUDETEAN','INSPECTORATUL ȘCOLAR AL JUDEȚULUI','INSPECTORATUL SCOLAR AL JUDETULUI',
              'CENTRUL DE RESURSE ȘI ASISTENȚĂ EDUCAȚIONALĂ'],
    'SCSPC':['CENTRUL SCOLAR DE EDUCATIE INCLUZIVA','LICEUL SPECIAL','ŞCOALA SPECIALĂ','CENTRUL ŞCOLAR PENTRU EDUCAŢIE INCLUZIVĂ','C.S E.I','C.S.E.I.',
            'CENTRUL DE EDUCATIE INCLUZIVA','CENTRUL ȘCOLAR DE EDUCAȚIE INCLUZIVĂ','CSEI','CENTRUL ȘCOLAR DE EDUCAŢIE INCLUZIVĂ',
            'CENTRUL ȘCOLAR PENTRU EDUCAȚIE INCLUZIVĂ','SCOALA SPECIALA','SCOALA SPECIALĂ','ȘCOALA SPECIALĂ','CU NEVOI SPECIALE',
            'CLASE SPECIALE','ȘC. SPEC.','CENTRUL JUDEȚEAN DE ASISTENȚĂ','CENTRUL SCOLAR PENTRU EDUCATIE INCLUZIVA',
             'CENTRUL SCOLAR PENTRU EDUCAȚIE INCLUZIVĂ','ȘCOALA GIMNAZIALĂ SPECIALĂ',
            'CENTRUL ŞCOLAR DE EDUCAŢIE INCLUZIVĂ'],
    'STRUCT':['STRUCTURA','STRUCT','(TIPUL S)','(TIPUL ST)','STRUCTURĂ A ŞCOLII','(ST)','(S)','/ST','/ ST','/S','- ST','-ST','-S','- S','S -','UT -','UT-','S-','/ S','ST/','/UT',' UT',
             ' ST S','ST/','(AR)','(UT)','. ST.',', S'],
    'PERSJ':['(TIPUL PJ)','( PJ)','P.J','/PJ','-PJ','(PJ)','PJ -','PJ-','- PJ','-PJ','/ PJ','(PJ )',' PJ','(PJ, S)'],
    '':['"','”','„',',,','„','”',' / ','*',',','MUNICIPIUL','COMUNA ','ORAS ','ORASUL ',' COM ',"'",'(TIPUL )','(TIPUL)',
       'CU PREDARE IN LIMBA MAGHIARA','ORAŞ ','PROGRAM SUPLIMENTAR','(CENTRU EDUCATIONAL CU CLASA PREGATITOARE)'],
    ' ':['COM.'],
    'NR. ':['NUMĂRUL','NUMARUL','NUMĂR','NUMAR']
}
to_clean2={
    'SGMZ#':['SCOALA GENERALĂ','SCOALA GENERALA','ŞCOALA GENERALĂ','ȘCOALA GENERALĂ','SCOALA GENERAL','GIMN.','SCOLA GIMNAZIALA',
             'COLA GIMNAZIALA','COALA GENERALA','SC CU CLS.','GIM. '],
    'SPRM#':['CU CLASELE I-IV','SGMZ CU CLS . I- IV'],
    'LICTEH#':[],
    'LISPRT#':[],
    'LITEOR#':['LICEUL'],
    'COLGNAT#':['COLEGIUL','COLEG ','COLEG. '],
    'GRDNRM#':['GRADINITA DE COPIII','GRĂDINIŢA DE COPII','GRADINITA DE COPII','GRADINITA','GRĂDINITA','GRĂDINIŢA','GRĂDINIŢA',
               'GRĂDINIŢĂ','GRĂDINIȚA','GRDINIȚA','GRADINIŢA','GRĂDĂNIŢA','GR.','GRADINIȚA','GRD.',
              'GRĂDINIȚĂ','GRIDINIŢA','GRĂD.','GRĂDINŢA','GĂDINIŢA','GRAD ','GRĂD ','GRAD.P.V.','GRAD.'],
    'GRDPLG#':[],
    'GRPSC#':[],    
    '':['STRUCT','PERSJ']    
}

#final clean BEFORE extending with location name
to_clean_after={
    'GROF MAJLATH GUSZTAV KAROLY':['GMGK'],
    'FRANCISC NEUMAN':['FRATII NEUMAN'],
    'ADY ENDRE':['ADY ENDRE SERAL-MAGHIARA','ADY ENDRE TEORETIC','ADY ENDRE PJ'],
    'LICEUL HENRI COANDA':['HENRY COAND BECLEAN'],
    'NAPSUGAR':['NAPSUGAR ODORHEIU SECUIESC'],
    'CURCUBEU':['FUNDATIA CURCUBEUL','FUNDATIA CURCUBEU'],
    'CONSTANTIN BRANCUSI':['C-TIN BRANCUSI'],
    'TARNAVENI':['T-VENI'],
    'TIRGU MURES':['TG. MURES','TARGU MURES','TG.M.','TG.MURES','TÎRGU MUREȘ','TÎRGU MUREŞ'],
    'SANGEORGIU DE MURES':['SANG.DE MURES'],
    'SFANTU GHEORGHE':['SF.GHE.','SF.GHEORGHE','SF. GHEORGHE','SF.GH.'],
    'LUDUS':['LUDUȘ','LUDUŞ'],
    'DUMBRAVENI':['D-VENI'],
    'TARGU LAPUS':['TG. LAPUS','TG.LAPUS'],
    'GHEORGHE MARINESCU':['GH.MARINESCU'],
    'DEALUL VIILOR':['D.VIILOR'],
    'ZAHARIA BOIU':['Z.BOIU'],
    'ROMULUS GUGA':['R.GUGA'],
    'MIERCUREA NIRAJULUI':['M-NIRAJ'],
    'MIERCUREA CIUC':['M-CIUC', 'M. CIUC'],
    'CLUJ-NAPOCA':['CLUJ NAPOCA'],
    'AL.I.CUZA':['ALEXANDRU IOAN CUZA'],
    
    #equivalencies
    'LICTEH':['GRPSC']
}

#final clean AFTER extending with location name
to_clean_after_location={
    'BERCHEZ':['REMETEA CHIOARULUI - BERCHEZ','REMETEA CHIOARULUI BERCHEZ']
}
full_replace={
    'PJ':'PERSJ',
    'ST':'STRUCT',
    'STRUCTURA':'STRUCT',
    'S':'STRUCT',
    'UT':'STRUCT'
}
to_clean_k=16

Test outcomes

In [4078]:
convert_ro=False
dk=dg[dg['Megye']==m][['ID','Év','Név','Település','telepules']].drop_duplicates().sort_values(by='Név') 
for d,i in enumerate(dk.T.iteritems()):
    nev=i[1]['Név'].upper()
    if convert_ro:
        nev=roman(nev)
    telepules=i[1]['telepules']
    clean_nev=cleaner(nev, telepules, overwrite_result[m], gov_clean,gov_parent, convert_ro=convert_ro, test=True)
    to_print=False
    for s in list(to_clean.keys())[:to_clean_k]:
        if s in clean_nev: to_print=False
#     if '#' in clean_nev:
#         if 'GRDD' not in clean_nev:
#             to_print=True
#     to_print=True
    if nev in full_replace: to_print=False
    if to_print:
        print(d,clean_nev,'|',telepules,'|',nev)

In [4079]:
convert_ro=False
dv=gov[gov['Judet']==megye[m]][['Cod SIIIR','Denumire','Denumire scurtă','Localitate','Localitate superioară']].drop_duplicates().sort_values(by='Denumire')
for d,i in enumerate(dv.T.iteritems()):
    nev=i[1]['Denumire'].upper()
    if True:
#     if nev in ['GRĂDINIŢA PP "CĂSUŢA PITICILOR" ARAD']:
        if convert_ro:
            nev=roman(nev)
        telepules=i[1]['Localitate']
        telepules=roman(telepules)
        clean_nev=cleaner(nev, telepules, overwrite_result[m], gov_clean, gov_parent, convert_ro=convert_ro, test=True)
        to_print=False
        for s in list(to_clean.keys())[:to_clean_k]:
            if s in clean_nev: to_print=False
    #     if '#' in clean_nev:
#         if telepules=='ARAD':
#             if 'GRD' in clean_nev:
#                 to_print=True
    #     to_print=True
        if nev in full_replace: to_print=False
        if to_print:
            print(d,clean_nev,'|',roman(clean_nev),'|',telepules,'|',nev,'|',roman(nev)) 

Guessing function

In [4080]:
def get_max_class(clean_nev):
    dx=dg.loc[dk[dk['clean_names']==clean_nev].index][osztalyok]
    dx.columns=osztalyoki
    dx=dx.dropna(how='all').dropna(how='all',axis=1).T
    maxes=[]
    for x in dx.columns:
        if len(dx[x].dropna().index)>0:
            maxes.append(max(dx[x].T.dropna().index))
        else:
            maxes.append(0)
    return np.round(np.mean(maxes),1)

def get_scores(nev,telepules,telepulesek,guesses={},nr='',locationless=2,penalty=0):
    nev2=nev.replace(telepules,'').strip().replace('  ',' ').replace('  ',' ')
    nev3=replacer(clean_nev.replace(telepules,'').strip(),{i:'' for i in list(to_clean.keys())[:to_clean_k]}).strip().replace('  ',' ').replace('  ',' ')
    telepulesek2=[t.replace(telepules,'') for t in telepulesek]
    telepulesek3=[t for t in telepulesek2 if len(t.split(' '))>2]
    if nr: limit=50
    else: limit=10
    #for scorer in [fuzz.ratio,fuzz.token_sort_ratio,fuzz.token_set_ratio]:
    for scorer in [fuzz.ratio,fuzz.token_sort_ratio,fuzz.partial_ratio]:
        #full match
        scores=process.extract(nev, telepulesek, scorer=scorer, limit=limit)
        for match in scores:
            guess,score=match
            score2=similar(nev,guess)*100
            if guess not in guesses: guesses[guess]=[]
            for i in range(2): #give bigger weights to with-location matches
                guesses[guess].append(score+penalty)
                guesses[guess].append(score2+penalty)
        #locationless match
        if (locationless>0):
            if (nev2!=nev):
                try:
                    if len(nev2.split(' '))>2:
                        scores=process.extract(nev2, telepulesek3, scorer=scorer, limit=limit)
                        for match in scores:
                            guess,score=match
                            score2=similar(nev2,guess)*100
                            #convert guess back to orignial guess with location included
                            guess=telepulesek[telepulesek2.index(guess)]
                            if guess not in guesses: guesses[guess]=[]
                            guesses[guess].append(score+penalty)
                            guesses[guess].append(score2+penalty)
                except: pass
        #locationless and typless match
        if (locationless>1):
            if ((nev3!=nev) and (nev3!=nev2)):
                try:
                    if len(nev3.split(' '))>2:
                        scores=process.extract(nev2, telepulesek3, scorer=scorer, limit=limit)
                        for match in scores:
                            guess,score=match
                            score2=similar(nev2,guess)*100
                            #convert guess back to orignial guess with location included
                            guess=telepulesek[telepulesek2.index(guess)]
                            if guess not in guesses: guesses[guess]=[]
                            guesses[guess].append(score+penalty)
                            guesses[guess].append(score2+penalty)
                except: pass
    return guesses

def get_match(nev,clean_nev,telepules,gov_clean,gov_parent,max_class,params,verbose=False):
    guesses={}
    nev=nev.upper()
    nev2=nev.replace(telepules,'').strip().replace('  ',' ').replace('  ',' ')
    nev3=replacer(clean_nev.replace(telepules,'').strip(),{i:'' for i in list(to_clean.keys())[:to_clean_k]}).strip().replace('  ',' ').replace('  ',' ')
    in_county_th=params[0]
    place_penalty=params[2]
    location_weight=params[3]
    parent_weight=params[4]
    county_weight=params[5]
    type_advantage=params[6]
    siiir_penalty=params[7]
    if verbose: 
        print('Nev:',nev,'\nNev2:',nev2,'\nNev3:',nev3,'\nClean nev:',clean_nev,'\nTelepules:',telepules,'\nMax class:',max_class)
    nr=''.join(filter(lambda x: x.isdigit(), clean_nev))
    if nr:
        locationless=2 #locationless 1 and typless 2 match
    else:
        locationless=1 #locationless 1 match
    for n in [clean_nev]: #nev too for some
        #first process within telepules
        for i in range(location_weight): #give bigger weights to in-location matches (hist bias)
            guesses=get_scores(n,telepules,list(gov_clean[telepules].keys()),guesses,nr,locationless,penalty=0)
        if verbose: 
            print('Best matches within location:\n',{i:np.mean(guesses[i]) for i in guesses})
        #then look in parent, if parent is different
        if max({i:np.mean(guesses[i]) for i in guesses}.values())<in_county_th:
            if telepules!=gov_parent[telepules]:
                if gov_parent[telepules] in gov_clean:
                    for i in range(parent_weight): #give slightly lower weights to parent-location matches (hist bias)
                        guesses=get_scores(n,telepules,list(gov_clean[gov_parent[telepules]].keys()),guesses,nr,locationless,penalty=place_penalty)
                    if verbose: 
                        print('Best matches within parent:\n',{i:np.mean(guesses[i]) for i in guesses})
        #then look in all other plcaes inside the county, penalize more
        if max({i:np.mean(guesses[i]) for i in guesses}.values())<in_county_th:
            for i in range(county_weight): #give even lower weights to county-location matches (hist bias)
                guesses=get_scores(n,telepules,[item for sublist in \
                        [list(gov_clean[t].keys()) for t in gov_clean] for item in sublist],guesses,nr,locationless,penalty=place_penalty*2)
            if verbose: 
                print('Best matches within county:\n',{i:np.mean(guesses[i]) for i in guesses})
    
    #filter multiple schools referenced in name by max class
    if ('GRD' not in clean_nev):
        if max_class>1:
            guesses={i:guesses[i] for i in guesses if 'GRD' not in i}
    if (('GRD' in clean_nev) and ('GMZ' in clean_nev)):
        if max_class<2:
            guesses={i:guesses[i] for i in guesses if 'GMZ' not in i}
        else:
            guesses={i:guesses[i] for i in guesses if 'GRD' not in i}
    if (('GMZ' in clean_nev) and ('PRM' in clean_nev)):
        if max_class<6:
            guesses={i:guesses[i] for i in guesses if 'GMZ' not in i}
        else:
            guesses={i:guesses[i] for i in guesses if 'PRM' not in i}
    if (('LITEOR' in clean_nev) and ('GMZ' in clean_nev)):
        if max_class<10:
            guesses={i:guesses[i] for i in guesses if 'LITEOR' not in i}
        else:
            guesses={i:guesses[i] for i in guesses if 'GMZ' not in i}
    if (('LICTEH' in clean_nev) and ('GMZ' in clean_nev)):
        if max_class<10:
            guesses={i:guesses[i] for i in guesses if 'LICTEH' not in i}
        else:
            guesses={i:guesses[i] for i in guesses if 'GMZ' not in i}
    if (('LITOLX' in clean_nev) and ('GMZ' in clean_nev)):
        if max_class<10:
            guesses={i:guesses[i] for i in guesses if 'LITOLX' not in i}
        else:
            guesses={i:guesses[i] for i in guesses if 'GMZ' not in i}
    if (('COLGNAT' in clean_nev) and ('GMZ' in clean_nev)):
        if max_class<10:
            guesses={i:guesses[i] for i in guesses if 'COLGNAT' not in i}
        else:
            guesses={i:guesses[i] for i in guesses if 'GMZ' not in i}
    if verbose: 
        print('Pruned by max class ('+str(max_class)+') to:\n',{i:np.mean(guesses[i]) for i in guesses})
    guesses={i:np.mean(guesses[i]) for i in guesses}
    
    #infer institution type and increase those scores
    if type_advantage>0:
        if max_class<2:
            guesses={i:guesses[i]+type_advantage if 'GRD' in i else guesses[i] for i in guesses}
        elif max_class<6:
            guesses={i:guesses[i]+type_advantage if 'PRM' in i else guesses[i] for i in guesses}
        elif max_class<10:
            guesses={i:guesses[i]+type_advantage if 'GMZ' in i else guesses[i] for i in guesses}
        if verbose: 
            print('Pruned by type to:\n',guesses)
    
    #if there is multiple digit matches, keep only perfect matches
    if nr:
        #configure to completely prune or just give number matching advantage
        #guesses={i:guesses[i] for i in guesses if nr in i}
        for i in guesses:
            i_nr=''.join(filter(lambda x: x.isdigit(), i))
            #for exact matches make the number advantage very high
            if i_nr==nr:
                guesses[i]+=20
                #for short names make the number advantage larger
                if len(i)<25:
                    guesses[i]+=10
                
        if verbose: 
            print('Pruned by "NR. X" to:\n',guesses)
    
    #penalize school highly unlikely to teach in Hungarian (not part of the 2017 list of SIIIRs)
    si={}
    for telepules in gov_clean:
        for iskola in gov_clean[telepules]:
            si[iskola]=gov_clean[telepules][iskola]['siiir']
    for i in guesses:
        if i in si:
            if si[i] not in siiir2017:
                #penalize only those not manually put in exceptions
                if i not in siiir_exceptions:
                    guesses[i]+=siiir_penalty
    if verbose: 
            print('Pruned by SIIIR to:\n',guesses)
    
    if len(guesses)>0:
        selected=(max(guesses, key=guesses.get),max(guesses.values()))
    else:
        selected=(clean_nev, 0)
    
    #if item is clearly GRD but does not exist as a separate institution, create new
    if ((selected[1]<(in_county_th+15))and(max_class<1)):
        selected=[selected[0],selected[1]] #convert from tuple to list
        selected[0]=selected[0].replace('SPRM','GRDNRMX').replace('SGMZ','GRDNRMX')
        selected[1]+=10
        if verbose: 
            print('Max class indicates GRD, overwritten to (new):',selected)  
    #if item is clearly SPRM but does not exist as a separate institution, create new
    if ((selected[1]<(in_county_th+15))and(max_class>1)and(max_class<5)):
        if 'GRD' in selected[0]:
            selected=[selected[0],selected[1]] #convert from tuple to list
            selected[0]=selected[0].replace('GRDNRM','SPRMX').replace('GRDPLG','SPRMX')
            selected[1]+=10
            if verbose: 
                print('Max class indicates SPRM, overwritten to (new):',selected)  
    
    if verbose: 
        print('Final choice:',selected)      
    return selected

Init params

In [4081]:
in_county_th=70 #score below which run entire county
new_th=45 #score below which to consider the school new
place_penalty=-10 #score penalty for looking in parent place
location_weight=3
parent_weight=2
county_weight=1
type_advantage=10
siiir_penalty=-15 #score pantly for school highly unlikely to teach in Hungarian
params=[in_county_th,new_th,place_penalty,location_weight,parent_weight,county_weight,type_advantage,siiir_penalty]
mparams[m]=params

Do the matching

In [4082]:
gov_clean, gov_parent=reset_gov(gov_clean,gov_parent)
clean_names=[]
for d,i in enumerate(dk.T.iteritems()):
    #name formatting
    nev=i[1]['Név'].upper()
    nev=roman(nev)
    telepules=i[1]['telepules']
    clean_nev=cleaner(nev, telepules, overwrite_result[m], gov_clean, gov_parent)
    clean_names.append(clean_nev)
dk['clean_names']=clean_names

Calculate `gov_clean`

In [4083]:
guessed_names={}
max_classes={}
for d,i in enumerate(dk.T.iteritems()):
    #name init
    nev=i[1]['Név']
    telepules=i[1]['telepules']
    clean_nev=i[1]['clean_names']
    if clean_nev not in guessed_names: 
        guessed_names[clean_nev]={}
        #infer max class
        max_classes[clean_nev]=get_max_class(clean_nev)        
    if telepules not in guessed_names[clean_nev]:
        
        locations={telepules:{'type':'data','confidence':100}}

        if 'LEORINTXXX' in clean_nev: verbose=True #for debug
        else: verbose=False
        
        #infer location from name
        ts=process.extract(clean_nev,list(gov_clean.keys()),limit=2)
        for t in ts:
            if t[1]>80: inferred_loc=t[0]
            else: inferred_loc=''
            if inferred_loc:
                if inferred_loc not in locations:
                    locations[inferred_loc]={'type':'from_name','confidence':t[1]}
                else:
                    locations[inferred_loc]['confidence']+=t[1]

        #infer location from telepules
        t=process.extractOne(telepules,list(gov_clean.keys()))
        if t[1]>90: inferred_loc=t[0]
        else: inferred_loc=''
        if inferred_loc:
            if inferred_loc not in locations:
                locations[inferred_loc]={'type':'from_loc','confidence':t[1]}
            else:
                locations[inferred_loc]['confidence']+=t[1]
        if verbose: 
            print(nev,clean_nev,locations)

        #extend locations with no matches
        for location in locations:
            if location not in guessed_names[clean_nev]: guessed_names[clean_nev][location]={}
            if location not in gov_parent: gov_parent[location]=location
            if location not in gov_clean:
                gov_clean[location]={}
                s=(location,0)
            else:
                s=get_match(nev,clean_nev,location,gov_clean,gov_parent,max_classes[clean_nev],params,verbose=verbose)
            if s[1]<new_th:
                if clean_nev not in gov_clean[location]:
                    gov_clean[location][clean_nev]={'index':'New school','siiir':0}
                    print('New school:',i[0],clean_nev,nev,telepules,location)
mgov_clean[m]=gov_clean

New school: 16360 GRDNRM JIGODIN BAI GPN JIGODIN BAI JIGODIN BAI
New school: 16362 GRDNRM CIOBOTENI GPN CIOBOTENI CIOBOTENI
New school: 16359 GRDNRM HARGHITA BAI GPN HARGHITA BAI HARGHITA BAI
New school: 7424 GRDNRM PAULENI-CIUC GRADINITA CU PROGRAM NORMAL PAULENI-CIUC / UT PAULENI CIUC PAULENI CIUC
New school: 7489 GRDNRM PETECU GRADINITA PETECU / UT PETECU PETECU
New school: 15267 LICTEH PUSKAS TIVADAR/ SGMZ JOLOTCA Liceul Tehnologic Puskas Tivadar/ Scoala Gimnaziala Jolotca-ST DITRAU DITRAU


C:\ProgramData\Anaconda3\lib\site-packages\numpy\core\fromnumeric.py:3335: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
C:\ProgramData\Anaconda3\lib\site-packages\numpy\core\_methods.py:161: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


New school: 14461 STRUCT CARTA S CARTA CARTA
New school: 11112 SCOALA BENEDEK ELEK FILIASI SCOALA "BENEDEK ELEK"FILIASI FILIASI FILIASI
New school: 8322 SPRM GHIPES SCOALA PRIMARA GHIPES / UT GHIPES GHIPES
New school: 8384 SPRM PETECU SCOALA PRIMARA PETECU / UT PETECU PETECU
New school: 8312 SPRM PALTINI CIUC SCOALA PRIMARA PĂLTINIȘ-CIUC / UT PALTINIS CIUC PALTINIS CIUC
New school: 490 LICTEH DE ARTE SI MESERII NR 16 SFANTA ANA MIERCUREA CIUC SCOALA PROFESIONALA DE ARTE SI MESERII NR 16 SFANTA ANA  MIERCUREA CIUC LUNCA DE JOS
New school: 8248 SPRM TELEAC SPRM TELEAC TELEAC
New school: 17518 SPRM JIGODIN BAI SPRM JIGODIN BAI JIGODIN BAI
New school: 17515 SPRM HARGHITA BAI SPRM HARGHITA BAI HARGHITA BAI
New school: 6056 SGMZ NR 4 PLAIESII DE SUS Sc Gim Nr 4 PLAIESII DE SUS PLAIESII DE SUS
New school: 11131 SGMZ FULOP ARON FELICENI PRM FORTENI ŞCOALA GIMNAZIALĂ FÜLÖP ÁRON FELICENI/SCOALA PRIMAR FORTENI FELICENI FELICENI
New school: 11132 SGMZ FULOP ARON FELICENI PRM HOGHIA ŞCOALA GIMNAZIA

In [4084]:
clean_names=[]
for d,i in enumerate(dk.T.iteritems()):
    #name formatting
    nev=i[1]['Név'].upper()
    nev=roman(nev)
    telepules=i[1]['telepules']
    clean_nev=cleaner(nev, telepules, overwrite_result[m], gov_clean, gov_parent)
    clean_names.append(clean_nev)
dk['clean_names']=clean_names

Calculate `guessed_names`

In [4085]:
in_county_th=new_th+10 #severely limit to search within location only since the the school database is now constructed
params=[in_county_th,new_th,place_penalty,location_weight,parent_weight,county_weight,type_advantage,siiir_penalty]
for clean_nev in guessed_names:
    for location in guessed_names[clean_nev]: 
        if True:
#         if 'GRD' in clean_nev and 'BRASOV' in clean_nev:
            dummy={}
            if clean_nev=='GRDNRM NR. 25 S BRASOVXXX':
                verbose=True
            else:
                verbose=False
            s=get_match(clean_nev,clean_nev,location,gov_clean,gov_parent,max_classes[clean_nev],params,verbose=verbose)
            if s[1]>new_th:
                dummy[s[0]]=s[1]
            else:
                dummy[clean_nev]=new_th-10
            guessed_names[clean_nev][location]=dummy

In [4086]:
#extremely punish location+parent occurences
verbose=False
for clean_nev in guessed_names:
    #extract top 2 locations
    #best_2_locations=process.extract(clean_nev,list(guessed_names[clean_nev].keys()),scorer=fuzz.token_sort_ratio,limit=2)
    best_2_locations=process.extract(clean_nev,list(guessed_names[clean_nev].keys()),scorer=fuzz.partial_ratio,limit=2)
    for location1 in guessed_names[clean_nev]:
        if len(best_2_locations)>1:
            #the top two mathcing locations are not equal have 
            if best_2_locations[0][1]>best_2_locations[1][1]:
                #then punish the rest                
                if location1!=best_2_locations[0][0]:
                    if verbose: print(0,location1,'is not best match for',clean_nev+', punishing a bit...')
                    guessed_names[clean_nev][location1]={i:guessed_names[clean_nev][location1][i]+place_penalty*1 for i in guessed_names[clean_nev][location1]}
        for location2 in guessed_names[clean_nev]: 
            if location1!=location2:
                if gov_parent[location1]==location2:
                    #but only those which are actually found in the name
                    if location1 in clean_nev:
                        if verbose: print(2,location2,'is parent of',location1,', punishing a lot...')
                        guessed_names[clean_nev][location2]={i:guessed_names[clean_nev][location2][i]+place_penalty*3 for i in guessed_names[clean_nev][location2]}
                    else:
                        if verbose: print(1,location2,'is parent of',location1,', but',location1,'is not in name, punishing a bit...')
                        guessed_names[clean_nev][location2]={i:guessed_names[clean_nev][location2][i]+place_penalty*1 for i in guessed_names[clean_nev][location2]}

In [4087]:
guessed_names_curated={}
guessed_names_list=[]
for clean_nev in guessed_names:
#     if True:
#     if 'SPRM' in clean_nev and 'PALEU' in clean_nev:
        max_name=''
        max_location=''
        max_value=0
        if clean_nev not in guessed_names_curated: guessed_names_curated[clean_nev]={}
        for location in guessed_names[clean_nev]: 
            for guess in guessed_names[clean_nev][location]:
                if guessed_names[clean_nev][location][guess]>max_value:
                    max_value=guessed_names[clean_nev][location][guess]
                    max_name=str(guess)
                    max_location=str(location)
        for location in guessed_names[clean_nev]: 
            guessed_names_curated[clean_nev][location]=max_name
            clean_nev_nr=''.join(filter(lambda x: x.isdigit(), clean_nev))
            if clean_nev_nr:
                max_nev_nr=''.join(filter(lambda x: x.isdigit(), max_name))
                #if numberred names don't match perfectly, raise a flag to investigate
                if clean_nev_nr!=max_nev_nr:
                    if int(clean_nev_nr)<5:
                        #but only slightly if numberred names are very small numbers
                        max_value+=place_penalty*2
                    else:
                        max_value+=place_penalty*4
                
            guessed_names_list.append({'telepules':location,'clean_names':clean_nev,'guessed_names':max_name,
                                       'guess_location':max_location,'guess_scores':np.int(np.round(max_value,0)),'max_class':max_classes[clean_nev]})

Post-processing

In [4088]:
dr=pd.DataFrame(guessed_names_list)
dr=dk.set_index(['telepules','clean_names']).join(dr.set_index(['telepules','clean_names']))

In [4089]:
#run post-overwrite queries here to avoid double-keying
overwrite_output={
    'Fehér': {},
    'Arad': {},
    'Bukarest': {},
    'Bákó': {},
    'Bihar': {
        'GRDNRM NR.6 SALONTA':'GRDPLG TOLDI SALONTA',
        'GRDNRM NR.7 SALONTA':'GRDPLG TOLDI SALONTA',
        'GRDNRM NR.9 SALONTA':'GRDPLG TOLDI SALONTA',
        'GRDNRM NR.10 SALONTA':'GRDPLG TOLDI SALONTA',
        'GRDNRM NR.12 SALONTA':'GRDPLG TOLDI SALONTA', #http://www.szalonta.ro/en/
        'LICTEH ANDREI SAGUNA ORADEA':'LITOLR LORANTFFY ZSUZSANNA ORADEA', #http://www.lorantffynagyvarad.ro/index.html
        'SPRM POCLUSA DE BARCAU':'SPRM NR.2 POCLUSA DE BARCAU'
    },
    'Beszterce-Naszód': {},
    'Brassó': {
        'GRDNRM NR. 4 SACELE':'GRDNRM NR. 4A SACELE', #inferred from years
        'GRDNRM NR. 1 SACELE':'GRDPLG NR. 1A SACELE' #inferred from years
    },
    'Kolozs': {
        'GRDPLG LUMEA PITICILOR DEJ':'GRDNRM LUMEA PITICILOR - 1 DEJ', #inferred from years
        'GRDNRM CASUTA PITICILOR - 1 TURDA':'GRDPLG CASUTA PITICILOR TURDA', #inferred from years
        'LICTEH TECHNOFRIG CLUJ-NAPOCA':'LICTEH NR. 1 CLUJ-NAPOCA',  #inferred from names
        'SPRM MONTESSORI SCHULE CLUJ-NAPOCA':'SGMZ MONTESSORI CLUJ-NAPOCA' #better fit
    },
    'Kovászna': {
        'GRDNRM DOBOLII DE SUS':'GRDNRM DOBOLII DE SUS BOROSNEU MARE',
        'SPRM DOBOLII DE SUS':'SPRM DOBOLII DE SUS BOROSNEU MARE',
        'GRDNRM LUTOASA':'GRDNRM LUTOASA MERENI',
        'SPRM LUTOASA':'SPRM LUTOASA MERENI',
        'GRDNRM TINOASA':'GRDNRM TINOASA LUNGA',
        'SPRM TINOASA':'SPRM TINOASA LUNGA',
        'SPRM TINOASA TARGU SECUIESC':'SPRM TINOASA LUNGA',
        'GRDNRM TINOASA TARGU SECUIESC':'GRDNRM TINOASA LUNGA',
        'SGMZ SPECIALA SFANTU GHEORGHE':'SCSPC SFANTU GHEORGHE',
        'GRDNRM CENUSAREASA SFANTU GHEORGHE':'GRDPLG HOFEHERKE SFANTU GHEORGHE',
        'GRDNRM NR. 3 SFANTU GHEORGHE':'GRDPLG BENEDEK ELEK SFANTU GHEORGHE',
        'GRDNRM NR. 6 SFANTU GHEORGHE':'GRDPLG NAPSUGAR SFANTU GHEORGHE',
        #inferred from address http://sepsiszentgyorgy.ro/index.php?option=com_alphacontent&view=alphacontent&Itemid=125
        'GRDNRM NR. 1 OJDULA':'GRDNRM HANGYABOLY OJDULA'
    },
    'Krassó-Szörény': {},
    'Hunyad': {
        'GRDPLG NR. 1 ORASTIE':'GRDNRM CASUTA CU POVESTI ORASTIE', #from parent institution
    },
    'Hargita': {
        'GRDNRM NR. 6 TORPIKEK CIUMANI':'GRDNRM CSALOKA -2 CIUMANI',
        'GRDNRM NR. 1 DITRAU':'GRDNRM CSIGABIGA DITRAU',
        'GRDNRM NR. 2 DITRAU':'GRDNRM ESZTERLANC DITRAU',
        'GRDNRM NR. 3 DITRAU':'GRDNRM CSIGABIGA DITRAU',
        'GRDNRM NR. 5 JOSENI':'GRDNRM MEHECSKE JOSENI',
        'GRDNRM NR. 6 JOSENI':'GRDNRM BECEVARI JOSENI',
        'GRDNRM NR. 2 JOSENI':'GRDNRM KOZPONTI JOSENI',
        'GRDNRM NR. 3 JOSENI':'GRDNRM ALSZEG JOSENI',
        'GRDNRM NR. 4 JOSENI':'GRDNRM MANO JOSENI',
        'GRDNRM TIPE-TUPA JOSENI':'GRDNRM KOZPONTI JOSENI',
        'GRDNRM NR. 1 JOSENI':'GRDNRM MESEVAR JOSENI',
        'SGMZ NR 4 LUNCA DE SUS':'SGMZ DOMOKOS PAL PETER LUNCA DE SUS',
        'SGMZ NR. 6 REMETEA':'SGMZ FRATER GYORGY REMETEA',
        'GRDNRM NR. 5 REMETEA':'GRDNRM CENTRU REMETEA',
        'GRDNRM NR. 6 REMETEA':'GRDNRM ALSZEGI REMETEA',
        'GRDPLG REMETEA':'GRDNRM CENTRU REMETEA',
        'GRDNRM NR. 2 REMETEA':'GRDNRM CENTRU REMETEA',
        'GRDNRM NR. 4 REMETEA':'GRDNRM CIUTAC REMETEA CIUTAC',
        'GRDNRM NR. 1 SANDOMINIC':'GRDNRM UGRI-BUGRI SANDOMINIC',
        'GRDNRM NR. 2 SANDOMINIC':'GRDNRM VIHANCKA SANDOMINIC'
    },
    'Máramaros': {},
    'Maros': {
        'GRDNRM NR. 5 REGHIN':'GRDNRM VOINICEL REGHIN', #inferred from data
        'GRDPLG NR. 1 TARNAVENI':'GRDPLG NR. 5 TARNAVENI', #inferred from address
        'GRDPLG NR. 2 LUDUS':'GRDNRM CASUTA FERMECATA LUDUS', #inferred from data
        'GRDNRM NR.2 LUDUS':'GRDNRM CASUTA FERMECATA LUDUS', #inferred from data
        'GRDNRM NR. 7 TIRGU MURES':'GRDPLG RANDUNICA TIRGU MURES', #https://www.govserv.org/RO/Targu-Mures/370004299745707/Gr%C4%83dini%C5%A3a-%22Randunica%22-T%C3%AErgu-Mure%C5%9F
        'GRDNRM NR. 14 TIRGU MURES':'GRDPLG RANDUNICA TIRGU MURES', #inferred from data
        'GRDNRM NR. 19 TIRGU MURES':'GRDPLG NR 16 TIRGU MURES', #inferred from parent
        'GRDNRM DACIA TIRGU MURES':'GRDPLG NR 16 TIRGU MURES', #inferred from parent
        'GRDPLG NR. 19 TIRGU MURES':'GRDPLG NR 10 TIRGU MURES', #inferred from parent
        'GRDNRM NR. 13 TIRGU MURES':'GRDPLG MANPEL TIRGU MURES', #inferred from data
        'GRDPLG NR. 13 TIRGU MURES':'GRDPLG ALBINUTA TIRGU MURES', #inferred from data
        'GRDNRM NR. 5 TIRGU MURES':'GRDPLG NR.15 TIRGU MURES', #inferred from parent address
        'LITOLC TIRGU MURES':'LITOLC II. RAKOCZI FERENC TIRGU MURES', # inferred from data
        'GRDNRM GEORGE COSBUC TIRGU MURES':'GRDPLG CODRISOR TIRGU MURES', #inferred from parent
        'GRDPLG NR. 9 TIRGU MURES':'GRDPLG CODRISOR TIRGU MURES', #inferred from data
        'GRDPLG NR. 6 TIRGU MURES':'GRDPLG STEFANIA TIRGU MURES', #inferred from data
        'GRDPLG NR. 3 TIRGU MURES':'GRDPLG ARLECHINO TIRGU MURES', #inferred from data
        'SPRM FANATE SINCAI':'SPRM SINCAI - FANATE', #inferred from data
        'GRDNRM ROZMARIN TIRGU MURES':'CENTRUL ROZMARIN TIRGU MURES',
        'GRDNRM GANESTI':'GRDPLG GANESTI'
    },
    'Szeben': {
        'GRDPLG NR. 12 MEDIAS':'GRDNRM NR. 1 MEDIAS', #inferred from names
        'LIARTE SATU MARE':'LIARTE AUREL POPP SATU MARE'
    },
    'Szatmár': {},
    'Szilágy': {},
    'Temes': {}
}

In [4090]:
dr['guessed_names2']=dr['guessed_names'].replace(overwrite_output[m])
dw=dr.groupby(['guessed_names2']).count()[['ID']]
dw.columns=['count']
dr=dr.reset_index().set_index('guessed_names2').join(dw).reset_index()
dr=dr[['ID','Év','telepules','guess_location','Név','clean_names','guessed_names2','Település','guess_scores','guessed_names','count','max_class']]
dr.to_excel('data/clean/guessed/'+m+'.xlsx')

Run all counties, then save:

In [4091]:
open('data/clean/mgov_clean.json','w').write(json.dumps(mgov_clean))
open('data/clean/mparams.json','w').write(json.dumps(mparams))

854

...testing area...

In [4092]:
# guessed_names_curated['SGMZ VAIDA CAMARAS CAIANU ST']

In [4093]:
# dr[dr['ID']==15323]['clean_names'].values

In [4094]:
# dr[dr['guessed_names2']=='SPRM SANTAUL MIC'].sort_values(by='Év')

In [4095]:
np.sort(dv['Localitate'].unique())

array(['ALDEA', 'ARMĂŞENI', 'ATIA', 'ATID', 'AVRĂMEŞTI', 'BANCU',
       'BARAŢCOŞ', 'BECAŞ', 'BETA', 'BILBOR', 'BISERICANI', 'BODOGAIA',
       'BORSEC', 'BORZONT', 'BRĂDEŞTI', 'BULGĂRENI', 'BÂRZAVA',
       'BĂILE TUŞNAD', 'BĂLAN', 'CAPU CORBULUI', 'CASINU NOU', 'CECHEŞTI',
       'CETĂŢUIA', 'CHILENI', 'CICEU', 'CIUCANI', 'CIUCSÂNGEORGIU',
       'CIUMANI', 'COBĂTEŞTI', 'COMIAT', 'COMĂNEŞTI', 'CORBU', 'CORUND',
       'COZMENI', 'CRISTURU SECUIESC', 'CRIŞENI', 'CRĂCIUNEL', 'CUŞMED',
       'CÂRŢA', 'CĂLNACI', 'CĂPÂLNIŢA', 'DAIA', 'DEALU', 'DELNIŢA',
       'DITRĂU', 'DOBENI', 'DÂRJIU', 'DĂNEŞTI', 'EGHERSEC', 'ELISENI',
       'FELICENI', 'FILPEA', 'FIRTUŞU', 'FIRTĂNUŞ', 'FORŢENI', 'FRUMOASA',
       'FUNDOAIA', 'FÂNCEL', 'FÂNTÂNA BRAZILOR', 'GHEORGHENI', 'GOAGIU',
       'GÂRCIU', 'GĂLĂUŢAŞ', 'HARGHITA-BĂI', 'HODOŞA', 'HOGHIA',
       'IACOBENI', 'IMPER', 'INEU', 'IZVOARE', 'IZVORU MUREŞULUI',
       'IZVORUL TROTUŞULUI', 'JIGODIN-BĂI', 'JOLOTCA', 'JOSENI',
       'LACU ROŞU', 'LIVE

In [4096]:
loc='OTELEC'
try:
    loc=loc.upper()
    telepules=roman(loc)
    for i in gov_clean[roman(loc)]:
        print(i,gov_clean[roman(loc)][i])
    display(dv[dv['Localitate']==loc])
except: pass

In [4097]:
# for i in dv[dv['Localitate']==loc].T.iteritems():
#     if 'NR' in i[1]['Denumire'].upper():
#         print(i[1]['Denumire'],'-------------',cleaner(roman(i[1]['Denumire']), roman(loc), overwrite_result[m], gov_clean, gov_parent, convert_ro=True, test=False))

In [4098]:
school='SGMZ CAPUSU MARE CAPUSU MARE'
print(dr[dr['guessed_names']==school]['Név'].unique())
dr[dr['guessed_names']==school].sort_values(by='Év')

[]


Empty DataFrame
Columns: [ID, Év, telepules, guess_location, Név, clean_names, guessed_names2, Település, guess_scores, guessed_names, count, max_class]
Index: []

In [4099]:
# in_county_th=55
# params=[in_county_th,new_th,place_penalty,location_weight,parent_weight,county_weight,type_advantage,siiir_penalty]
clean_nev='LICTEH TRANSILVANIA TIRGU MURES'
loc=clean_nev.split(' ')[-1:]
loc='TIRGU MURES'
try: 
    get_match(clean_nev, clean_nev, loc, gov_clean, gov_parent, 0.9, params, verbose=True)
    print(guessed_names[clean_nev])
except: pass

Nev: LICTEH TRANSILVANIA TIRGU MURES 
Nev2: LICTEH TRANSILVANIA 
Nev3: TRANSILVANIA 
Clean nev: LICTEH TRANSILVANIA TIRGU MURES 
Telepules: TIRGU MURES 
Max class: 0.9


Display all per loc

In [4100]:
# with pd.option_context('display.max_rows', None, 'display.max_columns', None):
#      display(dg[((dg['telepules']=='SUPLACU DE BARCAU'))].groupby(['Év','Név']).count().T.sum())

In [4101]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
     display(dr[(dr['guess_location']=='CLUJ NAPOCA'.strip())].sort_values(by=['guess_scores','count','guessed_names2']))

Empty DataFrame
Columns: [ID, Év, telepules, guess_location, Név, clean_names, guessed_names2, Település, guess_scores, guessed_names, count, max_class]
Index: []

In [4102]:
k=0

In [4103]:
# loc=dr[((dr['count']<3)&(0<dr['count']))].drop_duplicates(subset=['guessed_names2']).\
#              set_index(['guess_location','guessed_names2'])[['count']].sort_values(by=['count']).\
#              sort_index().index.get_level_values(0)[k]
# k+=1
# print(k,loc)
# print("'"+loc+"':['GRDNRM "+loc+"'],")
# with pd.option_context('display.max_rows', None, 'display.max_columns', None):
#      display(dr[(dr['guess_location']==loc.strip())].sort_values(by=['guess_scores','guessed_names2']))

Histogram

In [4104]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
     display(dr[((dr['count']<3)&(1<dr['count']))].drop_duplicates(subset=['guessed_names2']).\
             set_index(['guess_location','guessed_names2'])[['count']].sort_values(by=['count']).\
             sort_index()[0:])

count
guess_location    guessed_names2                                  
ALUNIS            SPRM ALUNIS                                    2
BISERICANI        GRDNRM BISERICANI                              2
CARTA             STRUCT CARTA                                   2
CHILENI           GRDNRM CHILENI                                 2
CIUCSANGEORGIU    SGMZ CINOD CIUCSANGEORGIU                      2
DIAFALAU          GRDNRMX DIAFALAU                               2
FILIASI           SCOALA BENEDEK ELEK FILIASI                    2
GHEORGHENI        CENTRU NAPSUGAR AZ ESOBEN SCSPC GHEORGHEN      2
                  LICTEH CON DE MASINI GHEORGHENI                2
GHIPES            SPRM GHIPES                                    2
JIGODIN BAI       SPRM JIGODIN BAI                               2
LAZARESTI         GRDNRM LAZARESTI                               2
LUNCA DE SUS      GRDNRM NR. 3 PALTINIS CIUC LUNCA DE SUS        2
LUPENI            GRDNRM LUPENI                                  2
MIERCUREA CIUC    GRDNRM JIGODIN MIERCUREA CIUC                  2
                  LICTEH SPECIALA SZENT ANNA MIERCUREA CIUC      2
MORARENI          GRDNRM MORARENI                                2
OCNA DE SUS       GRDNRM OCNA DE SUS                             2
ODORHEIU SECUIESC LITEOR MARIN PREDA ODORHEIU SECUIESC           2
                  SCSPC FUNDATIA ORBAN ODORHEIU SECUIESC         2
OTENI             GRDNRM OTENI                                   2
PALTINIS          GRDNRM PALTINIS LUPENI                         2
PRAID             GRDNRM PRAID                                   2
SUB CETATE        GRDNRM SUB CETATE                              2
TAURENI           GRDNRMX TAURENI                                2
TULGHES           SPRM TULGHE VALEA FRUMOASA                     2
VALEA BOROS       GRDNRM VALEA BOROS                             2
VALEA STRAMBA     GRDNRM VALEA STRAMBA                           2
VALEA UGRA        SPRM UGRA                                      2

Verify guesses

New schools

In [4105]:
dr[dr['guess_scores']<new_th].sort_values(by=['guess_scores','count'])

ID    Év     telepules guess_location  \
183   1569  2011        SUSENI        CHILENI   
4144  2413  2011  LUNCA DE SUS   VALEA GARBEA   
1134  1458  2011         BANCU          CINOD   
4423  2505  2011      MARTINIS          RARES   
4059  2514  2011        MUGENI         DOBENI   
...    ...   ...           ...            ...   
4056  2439  2011  PAULENI CIUC        DELNITA   
4005  2501  2011      MARTINIS      COMANESTI   
986   1613  2011        DITRAU        JOLOTCA   
2873  2598  2011        DITRAU        JOLOTCA   
4482  2553  2011        SUSENI         SUSENI   

                                         Név  \
183             Grădinița nr. 5 Chileni (ST)   
4144      Școala Generală nr. 5 Valea Gârbea   
1134              Grădinița nr. 6 Cinod (ST)   
4423            Școala Generală nr. 12 Rareș   
4059            Școala Generală nr. 9 Dobeni   
...                                      ...   
4056           Școala Generală nr. 2 Delnița   
4005         Școala Generală nr. 7 Comănești   
986    Grădinița nr. 5 Jolotca Tilalmas (ST)   
2873  Școala Generală nr. 4 Jolotca Tilalmas   
4482          Școala Generală nr. 3 Mureșeni   

                               clean_names                    guessed_names2  \
183                   GRDNRM NR. 5 CHILENI                    GRDNRM CHILENI   
4144  SGMZ NR. 5 VALEA GARBEA LUNCA DE SUS                       SPRM GARBEA   
1134                    GRDNRM NR. 6 CINOD         GRDNRMX NR. 5 CINOD BANCU   
4423                     SGMZ NR. 12 RARES                        SPRM RARES   
4059                     SGMZ NR. 9 DOBENI                       SPRM DOBENI   
...                                    ...                               ...   
4056       SGMZ NR. 2 DELNITA PAULENI CIUC                      SPRM DELNITA   
4005                  SGMZ NR. 7 COMANESTI                    SPRM COMANESTI   
986          GRDNRM NR. 5 JOLOTCA TILALMAS  GRDNRM TILALMAS JOLOTCA TILALMAS   
2873           SGMZ NR. 4 JOLOTCA TILALMAS                      SGMZ JOLOTCA   
4482            SGMZ NR. 3 MURESENI SUSENI           SPRM SUSENI - MURES SAT   

         Település  guess_scores                     guessed_names  count  \
183         Suseni            -4                    GRDNRM CHILENI      2   
4144  Lunca De Sus            13                       SPRM GARBEA      3   
1134         Bancu            14         GRDNRMX NR. 5 CINOD BANCU      3   
4423      Martinis            15                        SPRM RARES      3   
4059        Mugeni            21                       SPRM DOBENI      3   
...            ...           ...                               ...    ...   
4056  Pauleni-Ciuc            42                      SPRM DELNITA      7   
4005      Martinis            42                    SPRM COMANESTI      8   
986         Ditrau            43  GRDNRM TILALMAS JOLOTCA TILALMAS      4   
2873        Ditrau            43                      SGMZ JOLOTCA     19   
4482        Suseni            44           SPRM SUSENI - MURES SAT     12   

      max_class  
183         0.9  
4144        4.0  
1134        0.9  
4423        4.1  
4059        2.1  
...         ...  
4056        4.1  
4005        4.1  
986         0.9  
2873        4.1  
4482        4.1  

[75 rows x 12 columns]

Score bands

In [4106]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None): display(dr[((dr['guess_scores']<new_th+5)&(new_th-1<dr['guess_scores']))].sort_values(by=['guess_scores','count']))

ID    Év          telepules     guess_location  \
4509   2560  2011          SIMONESTI           TARCESTI   
4649  14496  2015              CARTA              CARTA   
4345   2490  2011       LUNCA DE SUS       LUNCA DE SUS   
2406   8280  2013            TOMESTI            TOMESTI   
3170  15232  2015              CINOD              CINOD   
1144   7434  2013        OCNA DE JOS        OCNA DE JOS   
144    1502  2011             LUPENI         BISERICANI   
3995   2430  2011     MIERCUREA CIUC     MIERCUREA CIUC   
1129   1474  2011             DARJIU              MUJNA   
4475   2431  2011     MIERCUREA CIUC     MIERCUREA CIUC   
3260    508  2010  ODORHEIU SECUIESC  ODORHEIU SECUIESC   
3294    489  2010     MIERCUREA CIUC     MIERCUREA CIUC   
3136   2542  2011         SANDOMINIC         SANDOMINIC   
3813  14469  2015     MIERCUREA CIUC     MIERCUREA CIUC   
4095   2583  2011            CIUMANI            CIUMANI   
2696  17648  2016            REMETEA            REMETEA   

                                                    Név  \
4509                     Școala Generală nr. 4 Tărcești   
4649                                                 PJ   
4345                Școala Generală nr. 3 Păltiniș Ciuc   
2406                 ŞCOALA PRIMARĂ TOMEŞTI/PRIMAR / PJ   
3170         Scoala Gimnaziala Cinod(ST cl. Frecv.red.)   
1144           GRADINITA DE COPII NR.4 OCNA DE JOS / UT   
144                      Grădinița nr. 3 Biserican (ST)   
3995                    Școala Generală nr. 6 Cioboteni   
1129                         Grădinița nr. 2 Mujna (ST)   
4475                    Școala Generală nr. 7 Subpădure   
3260  SCOALA GENERALA CLASELE I-VIII NR 7 MORA FEREN...   
3294  SCOALA GENERALA CLASELE I-VIII NR 12 NAGY IMRE...   
3136                   Școala Generală nr. 3 Sândominic   
3813                    Șc.Gim.Xantus Janos  17     238   
4095                      Școala Generală nr. 3 Ciumani   
2696       Sc. Gimn. Fráter György / Sc. Gen. Nr. 6 (S)   

                                          clean_names  \
4509                              SGMZ NR. 4 TARCESTI   
4649                                      PERSJ CARTA   
4345            SGMZ NR. 3 PALTINIS CIUC LUNCA DE SUS   
2406                              SPRM TOMESTI/PRIMAR   
3170                    SGMZ CINOD(ST CL. FRECV.RED.)   
1144                          GRDNRM NR.4 OCNA DE JOS   
144                     GRDNRM NR. 3 BISERICAN LUPENI   
3995              SGMZ NR. 6 CIOBOTENI MIERCUREA CIUC   
1129                               GRDNRM NR. 2 MUJNA   
4475              SGMZ NR. 7 SUBPADURE MIERCUREA CIUC   
3260  SGMZ NR 7 MORA FERENC ODORHEI ODORHEIU SECUIESC   
3294               SGMZ NR 12 NAGY IMRE MIERCURE-CIUC   
3136                            SGMZ NR. 3 SANDOMINIC   
3813          SGMZ XANTUS JANOS 17 238 MIERCUREA CIUC   
4095                               SGMZ NR. 3 CIUMANI   
2696                 SGMZ FRATER GYORGY NR. 6 REMETEA   

                          guessed_names2       Település  guess_scores  \
4509                       SPRM TARCESTI       Simonesti            46   
4649                        STRUCT CARTA           CIRTA            46   
4345          SPRM PALTINIS LUNCA DE SUS    Lunca De Sus            46   
2406          SGMZ BALINT VILMOS TOMESTI         TOMESTI            46   
3170            SGMZ MARTON FERENC BANCU           Cinod            46   
1144   GRDNRMX SUKOSD FERENC OCNA DE JOS     OCNA DE JOS            48   
144                    GRDNRM BISERICANI          Lupeni            48   
3995       SPRM CIOBOTENI MIERCUREA CIUC  Miercurea Ciuc            48   
1129                       GRDNRMX MUJNA          Dirjiu            48   
4475       SPRM SUBPADURE MIERCUREA CIUC  Miercurea Ciuc            48   
3260  SGMZ MORA FERENC ODORHEIU SECUIESC    ODORHEIU SEC            48   
3294       SGMZ NAGY IMRE MIERCUREA CIUC  MIERCUREA CIUC            48   
3136         SGMZ MARTON ARON SANDOMINIC      Sindominic            4

In [4107]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None): display(dr[((dr['guess_scores']<new_th+10)&(new_th+4<dr['guess_scores']))].sort_values(by=['guess_scores','count']))

ID    Év       telepules    guess_location  \
536    1585  2011       VOSLABENI  IZVORU MURESULUI   
4435   2521  2011          OCLAND          SATU NOU   
4480   8375  2013       SATU MARE         SATU MARE   
624   16442  2016           DEALU             DEALU   
2916    488  2010  MIERCUREA CIUC    MIERCUREA CIUC   
1059   1570  2011          SUSENI     VALEA STRAMBA   
1112   1420  2011        FELICENI            HOGHIA   
1135   7287  2013           CINOD             CINOD   
1136  13460  2015           CINOD             CINOD   
4264   5343  2012          LUTITA            LUTITA   
3865   5344  2012          ALUNIS            ALUNIS   
370    1579  2011           ULIES              DAIA   
537    7500  2013       VOSLABENI  IZVORU MURESULUI   
4172   2428  2011  MIERCUREA CIUC      HARGHITA-BAI   
142    1522  2011          MUGENI              BETA   
935    1574  2011       SIMONESTI         SIMONESTI   
1002   1558  2011        SICULENI          SICULENI   
3991   5383  2012         CHILENI           CHILENI   
872    1605  2011           PRAID             PRAID   
586    1599  2011           LUETA             LUETA   
265    1525  2011          OCLAND         CRACIUNEL   
3863   2499  2011        MARTINIS             ALDEA   
117    1514  2011       MIHAILENI         MIHAILENI   
4483   5382  2012          SUSENI            SUSENI   
3396    441  2010          BILBOR            BILBOR   
805    1505  2011          LUPENI          PALTINIS   
985    1614  2011          DITRAU           JOLOTCA   
430    1464  2011          CORUND  FANTANA BRAZILOR   
443    1593  2011           ZETEA             ZETEA   
621   13471  2015           DEALU             DEALU   
622    7317  2013           DEALU             DEALU   
623    4325  2012           DEALU             DEALU   
2447   6050  2012          LUTITA            LUTITA   
2545   2544  2011        SICULENI          SICULENI   

                                                    Név  \
536             Grădinița nr. 3  Izvorul Mureșului (ST)   
4435                     Școala Generală nr. 3 Satu Nou   
4480  ȘCOALA GIMNAZIALĂ ELEKES VENCEL SUSENI/ȘCOALA ...   
624                             Gr.nr.3 Dealu/structura   
2916  SCOALA GENERALA CLASELE I-VIII NR  8 JOZSEF AT...   
1059                Grădinița nr. 4 Valea  Strâmbă (ST)   
1112                        Grădinița nr. 4 Hoghia (ST)   
1135                               GRADINITA CINOD / UT   
1136                                    Gradinita Cinod   
4264                Scoala Generala Lutita Cu Cls. I-Iv   
3865                Scoala Generala Alunis Cu Cl . I-Iv   
370                           Grădinița nr. 2 Daia (ST)   
537   GRADINITA CU PROGRAM NORMAL NR.3 IZVORU MURESU...   
4172    Școala Generală nr. 4 Nyirő József Harghita-Băi   
142                           Grădinița nr. 2 Beta (ST)   
935                      Grădinița nr. 3 Mihăileni (ST)   
1002                 Grădinița nr. 2 Siculeni Gara (ST)   
3991                           Șc. Primară Nr.5 Chileni   
872                          Grădinița nr. 2 Praid (ST)   
586                          Grădinița nr. 1 Lueta (ST)   
265                      Grădinița nr. 2 Crăciunel (ST)   
3863                        Școala Generală nr. 2 Aldea   
117                      Grădinița nr. 1 Mihăileni (ST)   
4483                       Școala Primară Nr 3 Mureșeni   
3396  SCOALA GENERALA CLASELE I-VIII NR 1 OCTASLAUAN...   
805                       Grădinița nr. 2 Păltiniș (ST)   
985                        Grădinița nr. 4 Jolotca (ST)   
430               Grădinița nr. 2 Fântâna Brazilor (ST)   
443                        Grădinița nr. 3 Tofalău (ST)   
621                                      GR. NR.3 DEALU   
622                  GRADINITA DE COPII NR.3 DEALU / UT   
623                                      Gradinita Nr.3   
2447               Scoala Generala Lutita Cu Cls V-Viii   
2545                Școala Generală nr. 4 Siculeni Gara   

                 

In [4108]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None): display(dr[((dr['guess_scores']<new_th+20)&(new_th+9<dr['guess_scores']))].sort_values(by=['guess_scores','count']))

ID    Év          telepules      guess_location  \
606    1501  2011             LUPENI              LUPENI   
1145   1423  2011           FELICENI             TAURENI   
694    1520  2011             MUGENI              MUGENI   
3347  11087  2014              BANCU               CINOD   
944    1567  2011             SUSENI              SUSENI   
3188    510  2010       PAULENI CIUC        PAULENI-CIUC   
1846  15305  2015          SANMARTIN           SANMARTIN   
1847  14627  2015          SANMARTIN           SANMARTIN   
408    1543  2011           SECUIENI             ELISENI   
267    1446  2011               ATID             CRISENI   
915    1512  2011           MARTINIS             SANPAUL   
356    9819  2014          AVRAMESTI           AVRAMESTI   
4587   2467  2011              DEALU              ULCANI   
4574   2596  2011  CRISTURU SECUIESC   CRISTURU SECUIESC   
285    1597  2011            CIUMANI             CIUMANI   
2477    507  2010  ODORHEIU SECUIESC   ODORHEIU SECUIESC   
945    4415  2012             SUSENI              SUSENI   
3150   6051  2012           TAIETURA            TAIETURA   
3151   5345  2012           TAIETURA            TAIETURA   
68     1587  2011              ZETEA               ZETEA   
69     1588  2011              ZETEA               ZETEA   
696    1515  2011          MIHAILENI            NADEJDEA   
862    1422  2011           FELICENI            POLONITA   
4237  17701  2016              LUETA               LUETA   
4238  16559  2016              LUETA               LUETA   
392    1531  2011    PLAIESII DE JOS     PLAIESII DE JOS   
435    1418  2011           FELICENI            FELICENI   
643    1509  2011           MARTINIS            MARTINIS   
712    1578  2011              ULIES               ULIES   
808    1440  2011       PAULENI CIUC        PAULENI CIUC   
809    1441  2011       PAULENI CIUC        PAULENI CIUC   
469    1497  2011         VALEA RECE          VALEA RECE   
504    1560  2011               RACU                RACU   
3348  11971  2014              CINOD               CINOD   
3349   8988  2013              CINOD               CINOD   
3350   8277  2013              CINOD               CINOD   
3351  14495  2015              CINOD               CINOD   
3352  15231  2015              CINOD               CINOD   
4344  14532  2015       LUNCA DE SUS        LUNCA DE SUS   
3814  13430  2015     MIERCUREA CIUC      MIERCUREA CIUC   
583    1563  2011            COZMENI           LAZARESTI   
242    1573  2011          SIMONESTI           COBATESTI   
884    1571  2011          SIMONESTI           RUGANESTI   
1052   1516  2011          MIHAILENI           VACARESTI   
781    7404  2013           MISENTEA            MISENTEA   
934    1572  2011          SIMONESTI           SIMONESTI   
248    1508  2011           MARTINIS           COMANESTI   
976    1442  2011           BRADESTI           TARNOVITA   
807    1439  2011       PAULENI CIUC        PAULENI CIUC   
527   16430  2016           EGHERSEC            EGHERSEC   
821    1559  2011              CICEU               CICEU   
153    1581  2011             VARSAG              VARSAG   
154    1582  2011             VARSAG              VARSAG   
155    1583  2011             VARSAG              VARSAG   
156    1584  2011             VARSAG              VARSAG   
4208   2478  2011            LAZAREA             LAZAREA   
4209   2479  2011            LAZAREA             LAZAREA   
3118    444  2010           BRADESTI            BRADESTI   
4358   2497  2011             LUPENI             PAULENI   
888    1486  2011            LAZAREA             LAZAREA   
889    7357  2013            LAZAREA             LAZAREA   
890    4345  2012            LAZAREA             LAZAREA   
891    1487  2011            LAZAREA             LAZAREA   
2450  11199  2014             MUGENI              LUTITA   
2451  12030  2014             MUGENI              LUTITA   
2452   9945  2014             MUGENI             

In [4109]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None): display(dr[((dr['guess_scores']<new_th+30)&(new_th+19<dr['guess_scores']))].sort_values(by=['guess_scores','count']))

ID    Év          telepules      guess_location  \
1103   9821  2014          AVRAMESTI            CECHESTI   
1110   9820  2014          AVRAMESTI            FIRTANUS   
2275  17692  2016  ODORHEIU SECUIESC   ODORHEIU SECUIESC   
2044    528  2010          SUBCETATE           SUBCETATE   
4201   5408  2012            CIUMANI             CIUMANI   
4202   5409  2012            CIUMANI             CIUMANI   
4203   5410  2012            CIUMANI             CIUMANI   
1119  16384  2016            FORTENI             FORTENI   
253   13416  2015       LUNCA DE SUS              COMIAT   
851    7429  2013    PLAIESII DE SUS     PLAIESII DE SUS   
4410  11274  2014         VALEA RECE          VALEA RECE   
439   13425  2015            FORTENI             FORTENI   
906    1544  2011         SANCRAIENI             SANCRAI   
534    4439  2012            IZVOARE             IZVOARE   
3921  14572  2015           BODOGAIA            BODOGAIA   
2374  15266  2015        SOIMUSU MIC         SOIMUSU MIC   
2375   5360  2012        SOIMUSU MIC         SOIMUSU MIC   
2376   6059  2012        SOIMUSU MIC         SOIMUSU MIC   
2377   4396  2012        SOIMUSU MIC         SOIMUSU MIC   
3801  17656  2016         SANCRAIENI          SANCRAIENI   
1115  16544  2016   IZVORU MURESULUI    IZVORU MURESULUI   
1100  13538  2015           SECUIENI            SECUIENI   
1101   7464  2013           SECUIENI            SECUIENI   
1102   4399  2012           SECUIENI            SECUIENI   
4477   2426  2011     MIERCUREA CIUC      MIERCUREA CIUC   
1093   7336  2013            BARZAVA             BARZAVA   
1094   4334  2012            BARZAVA             BARZAVA   
1095  13481  2015            BARZAVA             BARZAVA   
1096   9877  2014           FRUMOASA             BARZAVA   
4050   8259  2013            DELNITA             DELNITA   
4594  14597  2015              ULIES               ULIES   
3944  11201  2014             MUGENI                BETA   
3945   9944  2014             MUGENI                BETA   
3983   8376  2013            CHILENI             CHILENI   
4518  11133  2014           FELICENI             TAURENI   
3512    518  2010             SARMAS              SARMAS   
899    9894  2014            LAZAREA             LAZAREA   
2563  13591  2015             DITRAU              DITRAU   
2564  15303  2015             DITRAU              DITRAU   
2565  14625  2015             DITRAU              DITRAU   
1934  15218  2015             BORSEC              BORSEC   
1935  14475  2015             BORSEC              BORSEC   
1125   1452  2011          AVRAMESTI              GOAGIU   
1126   7282  2013             GOAGIU              GOAGIU   
1127   4306  2012             GOAGIU              GOAGIU   
1141   1448  2011               ATID              SICLOD   
1142   7279  2013             SICLOD              SICLOD   
1143   4303  2012             SICLOD              SICLOD   
1116   9872  2014           FELICENI             FORTENI   
1117   4272  2012            FORTENI             FORTENI   
865    7333  2013           POLONITA            POLONITA   
237   16504  2016            REMETEA             REMETEA   
238   13534  2015            REMETEA             REMETEA   
4009  14640  2015       LUNCA DE SUS              COMIAT   
4228  11131  2014           FELICENI             FORTENI   
316    4249  2012             DITRAU              DITRAU   
3069    472  2010       LUNCA DE JOS        LUNCA DE JOS   
2991    449  2010            CIUMANI             CIUMANI   
181   13532  2015            REMETEA             REMETEA   
954    4414  2012             SUSENI              SUSENI   
3561    471  2010              LUETA               LUETA   
3137  11200  2014             MUGENI            TAIETURA   
3138  12031  2014             MUGENI            TAIETURA   
3139   9946  2014             MUGENI            TAIETURA   
2277  14556  2015             OCLAND              OCLAND   
3192   8260  2013            SOIMENI             

In [4110]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None): display(dr[((dr['guess_scores']<new_th+40)&(new_th+29<dr['guess_scores']))].sort_values(by=['guess_scores','count']))

ID    Év          telepules      guess_location  \
397   10012  2014            TOPLITA             TOPLITA   
815    9844  2014             CORUND              CORUND   
816    9845  2014             CORUND              CORUND   
817    7303  2013             CORUND              CORUND   
818   13464  2015             CORUND              CORUND   
819    1462  2011             CORUND              CORUND   
837    7346  2013         GHEORGHENI          GHEORGHENI   
847    7342  2013         GHEORGHENI          GHEORGHENI   
2047  12657  2014            TOPLITA             TOPLITA   
2048  12656  2014            TOPLITA             TOPLITA   
2049  12655  2014            TOPLITA             TOPLITA   
2050  12654  2014            TOPLITA             TOPLITA   
4079  10029  2014          VOSLABENI    IZVORU MURESULUI   
109    9921  2014            MERESTI             MERESTI   
495    1485  2011            LAZAREA             LAZAREA   
4492  17689  2016            IZVOARE             IZVOARE   
60     1541  2011           SECUIENI            SECUIENI   
3889  17598  2016            BARZAVA             BARZAVA   
4456  11217  2014            SOIMENI             SOIMENI   
295    1443  2011           BRADESTI            BRADESTI   
633   16460  2016             JOSENI              JOSENI   
634    7347  2013             JOSENI              JOSENI   
635   13489  2015             JOSENI              JOSENI   
636    4342  2012             JOSENI              JOSENI   
3045  11171  2014           MARTINIS             SANPAUL   
3046  12016  2014           MARTINIS             SANPAUL   
3052  15254  2015            SANPAUL             SANPAUL   
3053  14541  2015            SANPAUL             SANPAUL   
3054   9058  2013            SANPAUL             SANPAUL   
3055   8323  2013            SANPAUL             SANPAUL   
3750   6039  2012       LUNCA DE JOS          VALEA RECE   
3751   5313  2012       LUNCA DE JOS          VALEA RECE   
3752  14525  2015       LUNCA DE JOS          VALEA RECE   
3140   3212  2011             MUGENI            TAIETURA   
3141   2516  2011             MUGENI            TAIETURA   
595    1498  2011       LUNCA DE SUS        LUNCA DE SUS   
2963  15260  2015             OCLAND              OCLAND   
3645   8374  2013      VALEA STRAMBA       VALEA STRAMBA   
76     7506  2013              ZETEA               ZETEA   
3734   5289  2012   FANTANA BRAZILOR     VALEA LUI PAVEL   
3831  11183  2014     MIERCUREA CIUC        HARGHITA-BAI   
3832   9935  2014     MIERCUREA CIUC        HARGHITA-BAI   
1473   9888  2014         GHEORGHENI          GHEORGHENI   
2149  15318  2015  ODORHEIU SECUIESC   ODORHEIU SECUIESC   
2150  14641  2015  ODORHEIU SECUIESC   ODORHEIU SECUIESC   
775   16472  2016       LUNCA DE SUS        LUNCA DE SUS   
1137   4353  2012       LUNCA DE JOS      POIANA FAGULUI   
1121   7409  2013             MUGENI            TAIETURA   
1122   4379  2012           TAIETURA            TAIETURA   
1123  16491  2016           TAIETURA            TAIETURA   
226    1455  2011     CIUCSANGEORGIU      CIUCSANGEORGIU   
233    1454  2011     CIUCSANGEORGIU      CIUCSANGEORGIU   
53     1476  2011           FRUMOASA             BARZAVA   
3955  13590  2015            DANESTI             DANESTI   
3632    541  2010            VLAHITA             VLAHITA   
4419   9900  2014       LUNCA DE JOS        LUNCA DE JOS   
4420   8304  2013       LUNCA DE JOS        LUNCA DE JOS   
4421   5310  2012       LUNCA DE JOS        LUNCA DE JOS   
4422   7361  2013       LUNCA DE JOS        LUNCA DE JOS   
4617   9876  2014           FELICENI              VALENI   
4620  16393  2016             VALENI              VALENI   
4621   4275  2012             VALENI              VALENI   
344    7391  2013     MIERCUREA CIUC      MIERCUREA CIUC   
3667  15289  2015          VOSLABENI           VOSLABENI   
3898   5415  2012              BECAS               BECAS   
3844    521  2010           SICULENI            S

In [4111]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None): display(dr[((dr['guess_scores']<new_th+50)&(new_th+39<dr['guess_scores']))].sort_values(by=['guess_scores','count']))

ID    Év          telepules     guess_location  \
45      452  2010  CRISTURU SECUIESC  CRISTURU SECUIESC   
3057   8331  2013             LIVEZI             LIVEZI   
2273  11112  2014            FILIASI            FILIASI   
2274  11113  2014            FILIASI            FILIASI   
2276   5405  2012  ODORHEIU SECUIESC  ODORHEIU SECUIESC   
4650  14498  2015              CARTA              CARTA   
273    1596  2011            CIUMANI            CIUMANI   
3895   8308  2013         VALEA RECE           BARATCOS   
3896  11273  2014         VALEA RECE           BARATCOS   
523   10025  2014            VLAHITA            VLAHITA   
524   10026  2014            VLAHITA            VLAHITA   
3630  11279  2014            VLAHITA            VLAHITA   
3631  12081  2014            VLAHITA            VLAHITA   
4394  13500  2015       LUNCA DE JOS     POIANA FAGULUI   
4395  14527  2015       LUNCA DE JOS     POIANA FAGULUI   
4564  16550  2016              ZETEA              ZETEA   
4565  16551  2016              ZETEA              ZETEA   
3324   1580  2011              ULIES          NICOLESTI   
3510  17651  2016             SARMAS             SARMAS   
3511  18287  2016             SARMAS             SARMAS   
731    4440  2012  CRISTURU SECUIESC  CRISTURU SECUIESC   
2917  16542  2016             VARSAG             VARSAG   
2733  13424  2015           FELICENI           FELICENI   
2734  15210  2015           FELICENI           FELICENI   
2735  14462  2015           FELICENI           FELICENI   
2540  11158  2014       LUNCA DE SUS       LUNCA DE SUS   
1984   9508  2013  ODORHEIU SECUIESC  ODORHEIU SECUIESC   
1985   9509  2013  ODORHEIU SECUIESC  ODORHEIU SECUIESC   
3827   9933  2014     MIERCUREA CIUC     MIERCUREA CIUC   
3828  11186  2014     MIERCUREA CIUC     MIERCUREA CIUC   
3829  11185  2014     MIERCUREA CIUC     MIERCUREA CIUC   
3830   9934  2014     MIERCUREA CIUC     MIERCUREA CIUC   
3836  11182  2014     MIERCUREA CIUC     MIERCUREA CIUC   
1514    480  2010     MIERCUREA CIUC     MIERCUREA CIUC   
367   16419  2016             CUSMED             CUSMED   
838   13436  2015         GHEORGHENI         GHEORGHENI   
866   16389  2016           POLONITA           POLONITA   
3914  14605  2015              ZETEA              ZETEA   
349    4305  2012          AVRAMESTI          AVRAMESTI   
350    1449  2011          AVRAMESTI          AVRAMESTI   
3947   4454  2012            DANESTI            DANESTI   
3948   1612  2011            DANESTI            DANESTI   
4606  17606  2016       LUNCA DE JOS        VALEA BOROS   
4607  16465  2016       LUNCA DE JOS        VALEA BOROS   
4608  11154  2014       LUNCA DE JOS        VALEA BOROS   
4609   9899  2014       LUNCA DE JOS        VALEA BOROS   
4610   5309  2012       LUNCA DE JOS        VALEA BOROS   
4611   4348  2012       LUNCA DE JOS        VALEA BOROS   
4612   7362  2013       LUNCA DE JOS        VALEA BOROS   
3811   4279  2012     MIERCUREA CIUC     MIERCUREA CIUC   
3812   5254  2012     MIERCUREA CIUC     MIERCUREA CIUC   
1512   3636  2011     MIERCUREA CIUC     MIERCUREA CIUC   
1513   3655  2011     MIERCUREA CIUC     MIERCUREA CIUC   
52    16390  2016        ALEXANDRITA        ALEXANDRITA   
271   16418  2016            CRISENI            CRISENI   
3935  14621  2015  CRISTURU SECUIESC  CRISTURU SECUIESC   
517   13529  2015    PLAIESII DE JOS         CASINU NOU   
647    1419  2011           FELICENI            FORTENI   
4060   5292  2012              DEALU              DEALU   
556   16527  2016          SANSIMION          SANSIMION   
4152  14582  2015             GARCIU             GARCIU   
3943  13522  2015               BETA               BETA   
199    4323  2012            MADARAS            MADARAS   
200    1466  2011            MADARAS            MADARAS   
2379   5358  2012            REMETEA            REMETEA   
2380   6058  2012            REMETEA            REMETEA   
2381  12054  2014            REMETEA            REMETEA 

In [4112]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None): display(dr[((dr['guess_scores']<new_th+100)&(new_th+49<dr['guess_scores']))].sort_values(by=['guess_scores','count']))

ID    Év           telepules      guess_location  \
103   16392  2016            ARVATENI            ARVATENI   
206   16399  2016           CIOBOTENI           CIOBOTENI   
490    4352  2012        LUNCA DE JOS        LUNCA DE JOS   
814    7489  2013              PETECU              PETECU   
874    4354  2012        LUNCA DE JOS        LUNCA DE JOS   
1057  13497  2015        LUNCA DE JOS        LUNCA DE JOS   
1085   4431  2012           VOSLABENI           VOSLABENI   
1374    490  2010      MIERCUREA CIUC        LUNCA DE JOS   
4444   5402  2012             SICASAU             SICASAU   
143    7371  2013          BISERICANI          BISERICANI   
546    7393  2013      MIERCUREA CIUC      MIERCUREA CIUC   
605    7370  2013              LUPENI              LUPENI   
691    7373  2013            MORARENI            MORARENI   
939   16552  2016          SUB CETATE          SUB CETATE   
4156   8322  2013              GHIPES              GHIPES   
4157   5333  2012              GHIPES              GHIPES   
4199  17555  2016         JIGODIN BAI         JIGODIN BAI   
4200  17553  2016         JIGODIN BAI         JIGODIN BAI   
158   13540  2015            BODOGAIA            BODOGAIA   
159    4400  2012            BODOGAIA            BODOGAIA   
160    7466  2013            SECUIENI            BODOGAIA   
165    1450  2011           AVRAMESTI            CECHESTI   
166    7281  2013            CECHESTI            CECHESTI   
167    4304  2012            CECHESTI            CECHESTI   
241   16534  2016           COBATESTI           COBATESTI   
368    7488  2013                DAIA                DAIA   
369   10016  2014               ULIES                DAIA   
378    4378  2012             DEJUTIU             DEJUTIU   
379    7408  2013              MUGENI             DEJUTIU   
380    1517  2011              MUGENI             DEJUTIU   
381    7425  2013             DELNITA             DELNITA   
382    4295  2012             DELNITA             DELNITA   
383   13443  2015             DELNITA             DELNITA   
384    7410  2013              DOBENI              DOBENI   
385    4380  2012              DOBENI              DOBENI   
455    1451  2011           AVRAMESTI            FIRTANUS   
457    4307  2012            FIRTANUS            FIRTANUS   
487    7438  2013              GARCIU              GARCIU   
488    4407  2012              GARCIU              GARCIU   
510   16396  2016        HARGHITA BAI        HARGHITA BAI   
535    4430  2012    IZVORU MURESULUI    IZVORU MURESULUI   
543   16397  2016         JIGODIN BAI         JIGODIN BAI   
544   16398  2016         JIGODIN BAI         JIGODIN BAI   
545   16400  2016         JIGODIN BAI         JIGODIN BAI   
585    7358  2013               LUETA               LUETA   
697    7403  2013            NADEJDEA            NADEJDEA   
698    4373  2012            NADEJDEA            NADEJDEA   
882   16535  2016           RUGANESTI           RUGANESTI   
1053   7402  2013           VACARESTI           VACARESTI   
1054   4374  2012           VACARESTI           VACARESTI   
3507    516  2010               SACEL               SACEL   
3508   9054  2013               SACEL               SACEL   
3509   8351  2013               SACEL               SACEL   
3881   8321  2013              BADENI              BADENI   
3882   5332  2012              BADENI              BADENI   
3957   5404  2012   ODORHEIU SECUIESC   ODORHEIU SECUIESC   
3958  17691  2016   ODORHEIU SECUIESC   ODORHEIU SECUIESC   
4057   8338  2013              DOBENI              DOBENI   
4058   5346  2012              DOBENI              DOBENI   
4329   8312  2013       PALTINIS CIUC       PALTINIS CIUC   
4330  20402  2017       PALTINIS CIUC       PALTINIS CIUC   
4331  20401  2017       PALTINIS CIUC       PALTINIS CIUC   
4424   8324  2013               RARES               RARES   
4425   5331  2012               RARES               RARES   
4531   8248  2013              TELEAC       